Movielens dataset analysis for movie recommendations using Spark in Azure
1. The goal is to Develop an end to end data pipeline using Microsoft Azure and Databricks Spark
2. Creating resource group, containers, Storage account, Databricks cluster,

This notebook will show you how to create and query a table or DataFrame that you uploaded to DBFS. DBFS is a Databricks File System that allows you to store data for querying inside of Databricks. This notebook assumes that you have a file already inside of DBFS that you would like to read from.

In [0]:
%run /Movie_lens/Auth_details

In [0]:
#Import libraries
import datetime
import pyspark.sql.functions as f
import pyspark.sql.types
import pandas as pd

from pyspark.sql.functions import year, month, dayofmonth
from pyspark.sql.functions import unix_timestamp, from_unixtime
from pyspark.sql import window
from pyspark.sql.functions import rank, min

Out[2]: [FileInfo(path='abfss://data-storagetarget@sgmovielens.dfs.core.windows.net/genome-scores.csv', name='genome-scores.csv', size=125829120),
 FileInfo(path='abfss://data-storagetarget@sgmovielens.dfs.core.windows.net/genome-tags.csv', name='genome-tags.csv', size=18103),
 FileInfo(path='abfss://data-storagetarget@sgmovielens.dfs.core.windows.net/links.csv', name='links.csv', size=1368578),
 FileInfo(path='abfss://data-storagetarget@sgmovielens.dfs.core.windows.net/movies.csv', name='movies.csv', size=3038099),
 FileInfo(path='abfss://data-storagetarget@sgmovielens.dfs.core.windows.net/ratings.csv', name='ratings.csv', size=125829120),
 FileInfo(path='abfss://data-storagetarget@sgmovielens.dfs.core.windows.net/tags.csv', name='tags.csv', size=38810332)]

In [0]:
# File location and type
file_location = "abfss://data-storagetarget@sgmovielens.dfs.core.windows.net/movies.csv"

file_type = "csv"



# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
 
df_movies = spark.read.format(file_type) \
      .option("inferSchema", infer_schema) \
      .option("header", first_row_is_header) \
      .option("sep", delimiter) \
      .load("abfss://data-storagetarget@sgmovielens.dfs.core.windows.net/movies.csv")
    
display(df_movies)

movieId title genres 1 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2 Jumanji (1995) Adventure|Children|Fantasy 3 Grumpier Old Men (1995) Comedy|Romance 4 Waiting to Exhale (1995) Comedy|Drama|Romance 5 Father of the Bride Part II (1995) Comedy 6 Heat (1995) Action|Crime|Thriller 7 Sabrina (1995) Comedy|Romance 8 Tom and Huck (1995) Adventure|Children 9 Sudden Death (1995) Action 10 GoldenEye (1995) Action|Adventure|Thriller 11 American President, The (1995) Comedy|Drama|Romance 12 Dracula: Dead and Loving It (1995) Comedy|Horror 13 Balto (1995) Adventure|Animation|Children 14 Nixon (1995) Drama 15 Cutthroat Island (1995) Action|Adventure|Romance 16 Casino (1995) Crime|Drama 17 Sense and Sensibility (1995) Drama|Romance 18 Four Rooms (1995) Comedy 19 Ace Ventura: When Nature Calls (1995) Comedy 20 Money Train (1995) Action|Comedy|Crime|Drama|Thriller 21 Get Shorty (1995) Comedy|Crime|Thriller 22 Copycat (1995) Crime|Drama|Horror|Mystery|Thriller 23 Assassins (1995) Action|Crime|Thriller 24 Powder (1995) Drama|Sci-Fi 25 Leaving Las Vegas (1995) Drama|Romance 26 Othello (1995) Drama 27 Now and Then (1995) Children|Drama 28 Persuasion (1995) Drama|Romance 29 City of Lost Children, The (Cité des enfants perdus, La) (1995) Adventure|Drama|Fantasy|Mystery|Sci-Fi 30 Shanghai Triad (Yao a yao yao dao waipo qiao) (1995) Crime|Drama 31 Dangerous Minds (1995) Drama 32 Twelve Monkeys (a.k.a. 12 Monkeys) (1995) Mystery|Sci-Fi|Thriller 33 Wings of Courage (1995) Adventure|Romance|IMAX 34 Babe (1995) Children|Drama 35 Carrington (1995) Drama|Romance 36 Dead Man Walking (1995) Crime|Drama 37 Across the Sea of Time (1995) Documentary|IMAX 38 It Takes Two (1995) Children|Comedy 39 Clueless (1995) Comedy|Romance 40 Cry, the Beloved Country (1995) Drama 41 Richard III (1995) Drama|War 42 Dead Presidents (1995) Action|Crime|Drama 43 Restoration (1995) Drama 44 Mortal Kombat (1995) Action|Adventure|Fantasy 45 To Die For (1995) Comedy|Drama|Thriller 46 How to Make an American Quilt (1995) Drama|Romance 47 Seven (a.k.a. Se7en) (1995) Mystery|Thriller 48 Pocahontas (1995) Animation|Children|Drama|Musical|Romance 49 When Night Is Falling (1995) Drama|Romance 50 Usual Suspects, The (1995) Crime|Mystery|Thriller 51 Guardian Angel (1994) Action|Drama|Thriller 52 Mighty Aphrodite (1995) Comedy|Drama|Romance 53 Lamerica (1994) Adventure|Drama 54 Big Green, The (1995) Children|Comedy 55 Georgia (1995) Drama 56 Kids of the Round Table (1995) Adventure|Children|Comedy|Fantasy 57 Home for the Holidays (1995) Drama 58 Postman, The (Postino, Il) (1994) Comedy|Drama|Romance 59 Confessional, The (Confessionnal, Le) (1995) Drama|Mystery 60 Indian in the Cupboard, The (1995) Adventure|Children|Fantasy 61 Eye for an Eye (1996) Drama|Thriller 62 Mr. Holland's Opus (1995) Drama 63 Don't Be a Menace to South Central While Drinking Your Juice in the Hood (1996) Comedy|Crime 64 Two if by Sea (1996) Comedy|Romance 65 Bio-Dome (1996) Comedy 66 Lawnmower Man 2: Beyond Cyberspace (1996) Action|Sci-Fi|Thriller 67 Two Bits (1995) Drama 68 French Twist (Gazon maudit) (1995) Comedy|Romance 69 Friday (1995) Comedy 70 From Dusk Till Dawn (1996) Action|Comedy|Horror|Thriller 71 Fair Game (1995) Action 72 Kicking and Screaming (1995) Comedy|Drama 73 Misérables, Les (1995) Drama|War 74 Bed of Roses (1996) Drama|Romance 75 Big Bully (1996) Comedy|Drama 76 Screamers (1995) Action|Sci-Fi|Thriller 77 Nico Icon (1995) Documentary 78 Crossing Guard, The (1995) Action|Crime|Drama|Thriller 79 Juror, The (1996) Drama|Thriller 80 White Balloon, The (Badkonake sefid) (1995) Children|Drama 81 Things to Do in Denver When You're Dead (1995) Crime|Drama|Romance 82 Antonia's Line (Antonia) (1995) Comedy|Drama 83 Once Upon a Time... When We Were Colored (1995) Drama|Romance 84 Last Summer in the Hamptons (1995) Comedy|Drama 85 Angels and Insects (1995) Drama|Romance 86 White Squall (1996) Action|Adventure|Drama 87 Dunston Checks In (1996) Children|Comedy 88 Black Sheep (1996) Comedy 89 

movieId title genres 1 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2 Jumanji (1995) Adventure|Children|Fantasy 3 Grumpier Old Men (1995) Comedy|Romance 4 Waiting to Exhale (1995) Comedy|Drama|Romance 5 Father of the Bride Part II (1995) Comedy 6 Heat (1995) Action|Crime|Thriller 7 Sabrina (1995) Comedy|Romance 8 Tom and Huck (1995) Adventure|Children 9 Sudden Death (1995) Action 10 GoldenEye (1995) Action|Adventure|Thriller 11 American President, The (1995) Comedy|Drama|Romance 12 Dracula: Dead and Loving It (1995) Comedy|Horror 13 Balto (1995) Adventure|Animation|Children 14 Nixon (1995) Drama 15 Cutthroat Island (1995) Action|Adventure|Romance 16 Casino (1995) Crime|Drama 17 Sense and Sensibility (1995) Drama|Romance 18 Four Rooms (1995) Comedy 19 Ace Ventura: When Nature Calls (1995) Comedy 20 Money Train (1995) Action|Comedy|Crime|Drama|Thriller 21 Get Shorty (1995) Comedy|Crime|Thriller 22 Copycat (1995) Crime|Drama|Horror|Mystery|Thriller 23 Assassins (1995) Action|Crime|Thriller 24 Powder (1995) Drama|Sci-Fi 25 Leaving Las Vegas (1995) Drama|Romance 26 Othello (1995) Drama 27 Now and Then (1995) Children|Drama 28 Persuasion (1995) Drama|Romance 29 City of Lost Children, The (Cité des enfants perdus, La) (1995) Adventure|Drama|Fantasy|Mystery|Sci-Fi 30 Shanghai Triad (Yao a yao yao dao waipo qiao) (1995) Crime|Drama 31 Dangerous Minds (1995) Drama 32 Twelve Monkeys (a.k.a. 12 Monkeys) (1995) Mystery|Sci-Fi|Thriller 33 Wings of Courage (1995) Adventure|Romance|IMAX 34 Babe (1995) Children|Drama 35 Carrington (1995) Drama|Romance 36 Dead Man Walking (1995) Crime|Drama 37 Across the Sea of Time (1995) Documentary|IMAX 38 It Takes Two (1995) Children|Comedy 39 Clueless (1995) Comedy|Romance 40 Cry, the Beloved Country (1995) Drama 41 Richard III (1995) Drama|War 42 Dead Presidents (1995) Action|Crime|Drama 43 Restoration (1995) Drama 44 Mortal Kombat (1995) Action|Adventure|Fantasy 45 To Die For (1995) Comedy|Drama|Thriller 46 How to Make an American Quilt (1995) Drama|Romance 47 Seven (a.k.a. Se7en) (1995) Mystery|Thriller 48 Pocahontas (1995) Animation|Children|Drama|Musical|Romance 49 When Night Is Falling (1995) Drama|Romance 50 Usual Suspects, The (1995) Crime|Mystery|Thriller 51 Guardian Angel (1994) Action|Drama|Thriller 52 Mighty Aphrodite (1995) Comedy|Drama|Romance 53 Lamerica (1994) Adventure|Drama 54 Big Green, The (1995) Children|Comedy 55 Georgia (1995) Drama 56 Kids of the Round Table (1995) Adventure|Children|Comedy|Fantasy 57 Home for the Holidays (1995) Drama 58 Postman, The (Postino, Il) (1994) Comedy|Drama|Romance 59 Confessional, The (Confessionnal, Le) (1995) Drama|Mystery 60 Indian in the Cupboard, The (1995) Adventure|Children|Fantasy 61 Eye for an Eye (1996) Drama|Thriller 62 Mr. Holland's Opus (1995) Drama 63 Don't Be a Menace to South Central While Drinking Your Juice in the Hood (1996) Comedy|Crime 64 Two if by Sea (1996) Comedy|Romance 65 Bio-Dome (1996) Comedy 66 Lawnmower Man 2: Beyond Cyberspace (1996) Action|Sci-Fi|Thriller 67 Two Bits (1995) Drama 68 French Twist (Gazon maudit) (1995) Comedy|Romance 69 Friday (1995) Comedy 70 From Dusk Till Dawn (1996) Action|Comedy|Horror|Thriller 71 Fair Game (1995) Action 72 Kicking and Screaming (1995) Comedy|Drama 73 Misérables, Les (1995) Drama|War 74 Bed of Roses (1996) Drama|Romance 75 Big Bully (1996) Comedy|Drama 76 Screamers (1995) Action|Sci-Fi|Thriller 77 Nico Icon (1995) Documentary 78 Crossing Guard, The (1995) Action|Crime|Drama|Thriller 79 Juror, The (1996) Drama|Thriller 80 White Balloon, The (Badkonake sefid) (1995) Children|Drama 81 Things to Do in Denver When You're Dead (1995) Crime|Drama|Romance 82 Antonia's Line (Antonia) (1995) Comedy|Drama 83 Once Upon a Time... When We Were Colored (1995) Drama|Romance 84 Last Summer in the Hamptons (1995) Comedy|Drama 85 Angels and Insects (1995) Drama|Romance 86 White Squall (1996) Action|Adventure|Drama 87 Dunston Checks In (1996) Children|Comedy 88 Black Sheep (1996) Comedy 89 

In [0]:
# Create a view or table

temp_table_name = "movies_csv"

df_movies.createOrReplaceTempView(temp_table_name)

In [0]:
%sql

/* Query the created temp table in a SQL cell */

select * from `movies_csv`

movieId title genres 1 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2 Jumanji (1995) Adventure|Children|Fantasy 3 Grumpier Old Men (1995) Comedy|Romance 4 Waiting to Exhale (1995) Comedy|Drama|Romance 5 Father of the Bride Part II (1995) Comedy 6 Heat (1995) Action|Crime|Thriller 7 Sabrina (1995) Comedy|Romance 8 Tom and Huck (1995) Adventure|Children 9 Sudden Death (1995) Action 10 GoldenEye (1995) Action|Adventure|Thriller 11 American President, The (1995) Comedy|Drama|Romance 12 Dracula: Dead and Loving It (1995) Comedy|Horror 13 Balto (1995) Adventure|Animation|Children 14 Nixon (1995) Drama 15 Cutthroat Island (1995) Action|Adventure|Romance 16 Casino (1995) Crime|Drama 17 Sense and Sensibility (1995) Drama|Romance 18 Four Rooms (1995) Comedy 19 Ace Ventura: When Nature Calls (1995) Comedy 20 Money Train (1995) Action|Comedy|Crime|Drama|Thriller 21 Get Shorty (1995) Comedy|Crime|Thriller 22 Copycat (1995) Crime|Drama|Horror|Mystery|Thriller 23 Assassins (1995) Action|Crime|Thriller 24 Powder (1995) Drama|Sci-Fi 25 Leaving Las Vegas (1995) Drama|Romance 26 Othello (1995) Drama 27 Now and Then (1995) Children|Drama 28 Persuasion (1995) Drama|Romance 29 City of Lost Children, The (Cité des enfants perdus, La) (1995) Adventure|Drama|Fantasy|Mystery|Sci-Fi 30 Shanghai Triad (Yao a yao yao dao waipo qiao) (1995) Crime|Drama 31 Dangerous Minds (1995) Drama 32 Twelve Monkeys (a.k.a. 12 Monkeys) (1995) Mystery|Sci-Fi|Thriller 33 Wings of Courage (1995) Adventure|Romance|IMAX 34 Babe (1995) Children|Drama 35 Carrington (1995) Drama|Romance 36 Dead Man Walking (1995) Crime|Drama 37 Across the Sea of Time (1995) Documentary|IMAX 38 It Takes Two (1995) Children|Comedy 39 Clueless (1995) Comedy|Romance 40 Cry, the Beloved Country (1995) Drama 41 Richard III (1995) Drama|War 42 Dead Presidents (1995) Action|Crime|Drama 43 Restoration (1995) Drama 44 Mortal Kombat (1995) Action|Adventure|Fantasy 45 To Die For (1995) Comedy|Drama|Thriller 46 How to Make an American Quilt (1995) Drama|Romance 47 Seven (a.k.a. Se7en) (1995) Mystery|Thriller 48 Pocahontas (1995) Animation|Children|Drama|Musical|Romance 49 When Night Is Falling (1995) Drama|Romance 50 Usual Suspects, The (1995) Crime|Mystery|Thriller 51 Guardian Angel (1994) Action|Drama|Thriller 52 Mighty Aphrodite (1995) Comedy|Drama|Romance 53 Lamerica (1994) Adventure|Drama 54 Big Green, The (1995) Children|Comedy 55 Georgia (1995) Drama 56 Kids of the Round Table (1995) Adventure|Children|Comedy|Fantasy 57 Home for the Holidays (1995) Drama 58 Postman, The (Postino, Il) (1994) Comedy|Drama|Romance 59 Confessional, The (Confessionnal, Le) (1995) Drama|Mystery 60 Indian in the Cupboard, The (1995) Adventure|Children|Fantasy 61 Eye for an Eye (1996) Drama|Thriller 62 Mr. Holland's Opus (1995) Drama 63 Don't Be a Menace to South Central While Drinking Your Juice in the Hood (1996) Comedy|Crime 64 Two if by Sea (1996) Comedy|Romance 65 Bio-Dome (1996) Comedy 66 Lawnmower Man 2: Beyond Cyberspace (1996) Action|Sci-Fi|Thriller 67 Two Bits (1995) Drama 68 French Twist (Gazon maudit) (1995) Comedy|Romance 69 Friday (1995) Comedy 70 From Dusk Till Dawn (1996) Action|Comedy|Horror|Thriller 71 Fair Game (1995) Action 72 Kicking and Screaming (1995) Comedy|Drama 73 Misérables, Les (1995) Drama|War 74 Bed of Roses (1996) Drama|Romance 75 Big Bully (1996) Comedy|Drama 76 Screamers (1995) Action|Sci-Fi|Thriller 77 Nico Icon (1995) Documentary 78 Crossing Guard, The (1995) Action|Crime|Drama|Thriller 79 Juror, The (1996) Drama|Thriller 80 White Balloon, The (Badkonake sefid) (1995) Children|Drama 81 Things to Do in Denver When You're Dead (1995) Crime|Drama|Romance 82 Antonia's Line (Antonia) (1995) Comedy|Drama 83 Once Upon a Time... When We Were Colored (1995) Drama|Romance 84 Last Summer in the Hamptons (1995) Comedy|Drama 85 Angels and Insects (1995) Drama|Romance 86 White Squall (1996) Action|Adventure|Drama 87 Dunston Checks In (1996) Children|Comedy 88 Black Sheep (1996) Comedy 89 

In [0]:
# With this registered as a temp view, it will only be available to this particular notebook. If you'd like other users to be able to query this table, you can also create a table from the DataFrame.
# Once saved, this table will persist across cluster restarts as well as allow various users across different notebooks to query this data.
# To do so, choose your table name and uncomment the bottom line.

permanent_table_name = "movies_csv"

# df.write.format("parquet").saveAsTable(permanent_table_name)

In [0]:
#Read data "link"
links="/FileStore/tables/links.csv"
df_links = spark.read.format(file_type) \
      .option("inferSchema", infer_schema) \
      .option("header", first_row_is_header) \
      .option("sep", delimiter) \
      .load("abfss://data-storagetarget@sgmovielens.dfs.core.windows.net/links.csv")
    
display(df_links)

movieId imdbId tmdbId 1 114709 862 2 113497 8844 3 113228 15602 4 114885 31357 5 113041 11862 6 113277 949 7 114319 11860 8 112302 45325 9 114576 9091 10 113189 710 11 112346 9087 12 112896 12110 13 112453 21032 14 113987 10858 15 112760 1408 16 112641 524 17 114388 4584 18 113101 5 19 112281 9273 20 113845 11517 21 113161 8012 22 112722 1710 23 112401 9691 24 114168 12665 25 113627 451 26 114057 16420 27 114011 9263 28 114117 17015 29 112682 902 30 115012 37557 31 112792 9909 32 114746 63 33 114952 78802 34 112431 9598 35 112637 47018 36 112818 687 37 112286 139405 38 113442 33689 39 112697 9603 40 112749 34615 41 114279 31174 42 112819 11443 43 114272 35196 44 113855 9312 45 114681 577 46 113347 11861 47 114369 807 48 114148 10530 49 114916 8391 50 114814 629 51 109950 117164 52 113819 11448 53 110299 49133 54 112499 26441 55 113158 97406 56 113541 124057 57 113321 9089 58 110877 11010 59 112714 99040 60 113419 11359 61 116260 17182 62 113862 2054 63 116126 10607 64 118002 19760 65 115683 9536 66 116839 11525 67 114753 40628 68 113149 4482 69 113118 10634 70 116367 755 71 113010 11859 72 113537 28387 73 113828 48750 74 115644 20927 75 115676 36929 76 114367 9102 77 113973 124626 78 112744 27526 79 116731 9623 80 112445 46785 81 114660 400 82 112379 880 83 114039 146599 84 113612 188588 85 112365 8447 86 118158 10534 87 116151 17414 88 115697 13997 89 113972 2086 90 113490 61548 92 117002 9095 93 114825 12158 94 115639 9283 95 115759 9208 96 113403 40154 97 113247 406 98 111173 45549 99 113283 63076 100 115907 11062 101 115734 13685 102 117102 47475 103 118040 2045 104 116483 9614 105 112579 688 106 110251 11907 107 117110 10874 108 112646 89333 109 113276 96357 110 112573 197 111 75314 103 112 113326 33542 113 115645 43566 114 113774 71754 115 112556 43612 116 112373 51352 117 115033 16934 118 116606 10324 119 114536 78406 120 117427 55731 121 106473 32119 122 103859 11066 123 109424 11104 124 114808 37975 125 116324 2074 126 110647 27793 127 111055 44284 128 110217 290157 129 114131 110972 130 112364 32622 131 113107 73067 132 113451 11863 133 114015 55475 134 114500 124636 135 116130 9101 136 113125 123360 137 113756 5757 138 113952 39428 139 114618 124639 140 118055 9302 141 115685 11000 142 94878 525153 143 113200 249882 144 112585 16388 145 112442 9737 146 112342 30765 147 112461 10474 148 112427 22279 149 109093 30157 150 112384 568 151 114287 11780 152 112288 34996 153 112462 414 154 61395 649 155 112495 1873 156 112541 5894 157 109370 1775 158 112642 8839 159 112688 20649 160 112715 10329 161 112740 8963 162 109508 26564 163 112851 8068 164 112857 8512 165 112864 1572 166 112887 13552 167 113044 259209 168 113071 6520 169 113114 9073 170 113243 10428 171 113464 17447 172 113481 9886 173 113492 9482 174 113500 19326 175 113540 9344 176 113677 9071 177 113690 8973 178 107447 15730 179 113729 47608 180 113749 2293 181 113820 9070 182 113851 68274 183 110604 48787 184 110620 34574 185 113957 1642 186 113986 11472 187 114095 36196 188 114194 11980 189 114241 58372 190 114323 32646 191 114345 10533 192 114435 56088 193 114436 10802 194 114478 10149 195 114496 18402 196 114508 9348 197 114534 139408 198 114558 281 199 58450 5967 200 114666 79593 201 114663 47939 202 114702 36834 203 114682 9090 204 114781 3512 205 114798 52856 206 114805 77350 207 114887 9560 208 114898 9804 209 114928 31611 210 114938 65796 211 109340 49805 212 112602 26258 213 111579 50797 214 110882 19155 215 112471 76 216 112508 11017 217 112438 37141 218 112571 9382 219 112757 6715 220 112643 18256 222 112679 22625 223 109445 2292 224 112883 1909 225 109635 8984 226 112899 61813 227 109676 4954 228 112854 62488 229 109579 10531 230 109642 11929 231 109686 8467 232 111797 10451 233 109759 20156 234 109758 18395 235 109707 522 236 113117 397 237 113097 10525 238 113028 27985 239 113198 15789 240 113303 27303 241 113089 21183 242 109771 10954 243 113199 47867 244 113234 43475 245 109906 72031 246 110057 14275 247 110005 1024 248 110066 17207 249 110116 13

In [0]:
#Read data "tags"
tags="/FileStore/tables/tags.csv"
df_tags = spark.read.format(file_type) \
      .option("inferSchema", infer_schema) \
      .option("header", first_row_is_header) \
      .option("sep", delimiter) \
      .load("abfss://data-storagetarget@sgmovielens.dfs.core.windows.net/tags.csv")
    
display(df_tags)

userId movieId tag timestamp 3 260 classic 1439472355 3 260 sci-fi 1439472256 4 1732 dark comedy 1573943598 4 1732 great dialogue 1573943604 4 7569 so bad it's good 1573943455 4 44665 unreliable narrators 1573943619 4 115569 tense 1573943077 4 115713 artificial intelligence 1573942979 4 115713 philosophical 1573943033 4 115713 tense 1573943042 4 148426 so bad it's good 1573942965 4 164909 cliche 1573943721 4 164909 musical 1573943714 4 168250 horror 1573945163 4 168250 unpredictable 1573945171 19 2160 Oscar (Best Supporting Actress) 1446909853 19 7099 adventure 1445286141 19 7099 anime 1445286127 19 7099 ecology 1445286153 19 7099 fantasy 1445286144 19 7099 Hayao Miyazaki 1445286120 19 7099 Miyazaki 1445286148 19 7099 post-apocalyptic 1445286136 20 1210 bah 1155082282 43 434 Clint Eastwood 1170492549 68 3481 music 1472113217 84 194728 art 1549387440 84 194728 contemporary art 1549387437 84 194728 documentary 1549387432 87 1127 aliens 1542308477 87 1127 amazing photography 1542308501 87 1127 Director: James Cameron 1542308487 87 1127 first contact 1542308468 87 1127 James Cameron 1542308492 87 1127 Michael Biehn 1542308483 87 1127 sci-fi 1542308464 87 6537 android(s)/cyborg(s) 1542309549 87 6537 apocalypse 1542309703 87 6537 Arnold Schwarzenegger 1542309595 87 6537 artificial intelligence 1542309599 87 6537 franchise 1542309536 87 6537 terminator 1542309735 87 6537 time travel 1542309532 87 72998 James Cameron 1542308389 87 72998 sci-fi 1542308408 87 72998 science fiction 1542308395 87 79132 sci-fi 1522675497 87 102445 inferior sequel 1522677007 87 102445 setting:London (UK) (future) 1522677058 87 102445 unoriginal 1522677043 87 104841 bad science 1522676752 87 109487 good science 1522676693 87 109487 Hans Zimmer 1522676679 87 109487 philosophical issues 1522676687 87 109487 sci-fi 1522676660 87 109487 science fiction 1522676703 87 109487 space 1522676664 87 109487 space travel 1522676685 87 109487 time-travel 1522676667 87 109487 visually appealing 1522676682 91 215 bittersweet 1415131183 91 215 boring 1415914643 91 215 conversation 1415131159 91 215 dialogue driven 1415131169 91 215 loneliness 1415131180 91 215 love story 1415131196 91 215 philosophical 1415131228 91 215 philosophy 1415131215 91 215 quirky 1415914797 91 215 reflective 1415131174 91 215 romantic 1415131173 91 215 thought-provoking 1415131203 91 215 Vienna 1415914755 91 215 wistful 1415914789 91 590 American Civil War 1414248567 91 590 based on book 1414248543 91 590 bittersweet 1414248546 91 590 culture clash 1414248582 91 590 drama 1414248538 91 590 indians 1414248604 91 590 love story 1414248535 91 590 war 1414248586 91 590 western 1414248596 91 1619 Buddhism 1389309614 91 1619 China 1389309619 91 1619 great cinematography 1389309592 91 1619 JOURNEY OF SELF-DISCOVERY 1389309596 91 1619 mountains 1389309610 91 1619 traveling 1389309607 91 1719 atmospheric 1414932665 91 1719 based on a book 1414932650 91 1719 Canada 1414932654 91 1719 death 1414932717 91 1719 Incest 1414932657 91 1719 meditative 1414932635 91 1719 melancholic 1414932660 91 1719 Nudity (Full Frontal) 1414932679 91 1719 small town 1414932683 91 1719 wintry 1414932700 91 1962 aging 1414703813 91 1962 based on a play 1414703896 91 1962 boring 1414703922 91 1962 Drama 1414703854 91 1962 friendship 1414703861 91 1962 Morgan Freeman 1414703875 91 1962 no action 1414703922 91 1962 old age 1414703857 91 1962 racism 1414703880 91 1962 Southern theme 1414703882 91 1962 USA 1414703885 91 2324 bittersweet 1404508243 91 2324 emotional 1404508252 91 2324 heartwarming 1405162775 91 2324 Holocaust 1389309722 91 2324 Italy 1389309737 91 2324 love 1389309735 91 2324 Oscar (Best Foreign Language Film) 1404508261 91 2324 Oscar Winner 1404508239 91 2324 sentimental 1389309725 91 2324 survival 1404508257 91 2628 adventure 1406474907 91 2628 fantasy 1406474916 91 2628 music 1406474905 91 2628 Natalie Portman 1406474902 91 2628 robots 1406474862 91 2628 sci-fi 1406474865 91 2628 space 1406474897 91 2628 Star Wars 1406

In [0]:
#Read data "ratings"
ratings="/FileStore/tables/ratings.csv"
df_ratings = spark.read.format(file_type) \
      .option("inferSchema", infer_schema) \
      .option("header", first_row_is_header) \
      .option("sep", delimiter) \
      .load("abfss://data-storagetarget@sgmovielens.dfs.core.windows.net/ratings.csv")
    
display(df_ratings)

userId movieId rating timestamp 1 296 5.0 1147880044 1 306 3.5 1147868817 1 307 5.0 1147868828 1 665 5.0 1147878820 1 899 3.5 1147868510 1 1088 4.0 1147868495 1 1175 3.5 1147868826 1 1217 3.5 1147878326 1 1237 5.0 1147868839 1 1250 4.0 1147868414 1 1260 3.5 1147877857 1 1653 4.0 1147868097 1 2011 2.5 1147868079 1 2012 2.5 1147868068 1 2068 2.5 1147869044 1 2161 3.5 1147868609 1 2351 4.5 1147877957 1 2573 4.0 1147878923 1 2632 5.0 1147878248 1 2692 5.0 1147869100 1 2843 4.5 1147868891 1 3448 4.0 1147868480 1 3569 5.0 1147879603 1 3949 5.0 1147868678 1 4144 5.0 1147868898 1 4308 3.0 1147868534 1 4325 5.0 1147878122 1 4422 3.0 1147869048 1 4703 4.0 1147869223 1 4973 4.5 1147869080 1 5147 4.0 1147877654 1 5269 0.5 1147879571 1 5684 2.0 1147879797 1 5767 5.0 1147878729 1 5878 4.0 1147868807 1 5912 3.0 1147878698 1 5952 4.0 1147868053 1 6016 5.0 1147869090 1 6370 4.5 1147869191 1 6377 4.0 1147868469 1 6539 3.5 1147868461 1 6711 5.0 1147868622 1 6954 3.5 1147869150 1 7209 4.0 1147877986 1 7234 4.5 1147868869 1 7318 2.0 1147879850 1 7323 3.5 1147869119 1 7327 3.5 1147868855 1 7361 5.0 1147880055 1 7365 4.0 1147869033 1 7820 2.5 1147878050 1 7937 3.0 1147878055 1 7938 2.5 1147878063 1 7939 2.5 1147869183 1 7940 4.5 1147877967 1 8014 3.5 1147869155 1 8154 5.0 1147868865 1 8327 5.0 1147879375 1 8360 4.0 1147868682 1 8405 3.5 1147878095 1 8685 1.0 1147878023 1 8729 3.5 1147878452 1 8786 4.0 1147877853 1 8873 3.0 1147869094 1 8973 4.0 1147869211 1 27193 3.0 1147879774 1 27266 4.5 1147879365 1 27721 3.0 1147869115 1 31956 3.5 1147877610 1 32591 5.0 1147879538 2 1 3.5 1141415820 2 62 0.5 1141417130 2 110 5.0 1141416589 2 150 4.0 1141415790 2 151 4.5 1141415643 2 236 4.0 1141415659 2 260 5.0 1141417172 2 261 0.5 1141417855 2 266 1.0 1141415926 2 318 5.0 1141417181 2 333 5.0 1141415931 2 349 4.5 1141417045 2 356 4.5 1141416637 2 364 4.5 1141417077 2 380 1.0 1141415808 2 457 5.0 1141416618 2 480 2.0 1141417088 2 497 4.0 1141415566 2 524 3.5 1141417112 2 527 5.0 1141415816 2 534 4.5 1141417814 2 553 2.0 1141415539 2 588 2.0 1141417189 2 589 4.0 1141416748 2 653 3.0 1141415552 2 733 4.5 1141415905 2 858 3.5 1141416926 2 914 4.0 1141417642 2 953 4.5 1141417487 2 1035 1.0 1141415899 2 1080 1.0 1141415532 2 1136 5.0 1141417950 2 1196 5.0 1141417198 2 1197 5.0 1141415874 2 1198 4.0 1141417032 2 1201 2.5 1141415887 2 1210 5.0 1141416665 2 1246 4.0 1141416793 2 1257 5.0 1141417313 2 1270 4.0 1141417013 2 1271 1.5 1141417736 2 1275 4.5 1141417237 2 1283 4.0 1141416205 2 1287 5.0 1141417140 2 1291 5.0 1141416603 2 1293 5.0 1141417937 2 1299 1.0 1141416220 2 1302 3.0 1141417036 2 1356 5.0 1141417272 2 1374 4.5 1141415576 2 1376 5.0 1141417402 2 1393 4.0 1141417243 2 1431 3.0 1141416190 2 1465 3.0 1141417875 2 1485 3.0 1141415592 2 1488 5.0 1141416185 2 1527 3.0 1141417716 2 1580 4.5 1141417059 2 1584 5.0 1141416806 2 1587 1.0 1141416172 2 1610 5.0 1141416601 2 1653 4.5 1141415586 2 1672 4.5 1141417310 2 1674 4.0 1141417397 2 1682 4.5 1141415845 2 1693 4.0 1141417194 2 1722 0.5 1141415864 2 1873 4.0 1141416788 2 1907 4.0 1141417054 2 1923 0.5 1141417516 2 1957 3.5 1141416148 2 1968 1.0 1141415850 2 2028 4.0 1141415840 2 2081 1.5 1141415857 2 2083 4.5 1141417581 2 2115 3.5 1141417320 2 2138 4.5 1141416899 2 2139 4.0 1141416834 2 2150 5.0 1141418008 2 2194 5.0 1141415685 2 2268 4.5 1141416973 2 2273 2.0 1141416159 2 2294 4.5 1141416879 2 2324 1.5 1141417726 2 2355 4.5 1141416727 2 2359 5.0 1141417423 2 2406 2.5 1141415647 2 2470 5.0 1141415787 2 2496 4.0 1141416084 2 2501 4.5 1141416992 2 2571 5.0 1141416743 2 2617 4.0 1141415674 2 2640 5.0 1141415619 2 2643 0.5 1141416130 2 2694 4.0 1141416108 2 2720 0.5 1141416127 2 2745 5.0 1141416889 2 2761 0.5 1141417472 2 2762 4.0 1141415823 2 2797 1.0 1141415509 2 2918 4.5 1141417214 2 2987 0.5 1141417894 2 3098 3.0 1141417049 2 3105 4.0 1141417224 2 3107 3.0 1141416048 2 3114 4.5 1141416634 2 3148 2.0 1141417561 2 3175 3.5 1141417288 2 3360 5.0 1141417108 2 3396 4.5 1141417711 2 3479 2.0 1141416018 2 3510 4.0 1141416

In [0]:
#Read data "Genome_tags"
ratings="/FileStore/tables/genome-tags.csv"
df_genome= spark.read.format(file_type) \
      .option("inferSchema", infer_schema) \
      .option("header", first_row_is_header) \
      .option("sep", delimiter) \
      .load("abfss://data-storagetarget@sgmovielens.dfs.core.windows.net/genome-tags.csv")
    
display(df_genome)

tagId tag 1 007 2 007 (series) 3 18th century 4 1920s 5 1930s 6 1950s 7 1960s 8 1970s 9 1980s 10 19th century 11 3d 12 70mm 13 80s 14 9/11 15 aardman 16 aardman studios 17 abortion 18 absurd 19 action 20 action packed 21 adaptation 22 adapted from:book 23 adapted from:comic 24 adapted from:game 25 addiction 26 adolescence 27 adoption 28 adultery 29 adventure 30 affectionate 31 afi 100 32 afi 100 (laughs) 33 afi 100 (movie quotes) 34 africa 35 afterlife 36 aging 37 aids 38 airplane 39 airport 40 alaska 41 alcatraz 42 alcoholism 43 alien 44 alien invasion 45 aliens 46 allegory 47 almodovar 48 alone in the world 49 alter ego 50 alternate endings 51 alternate history 52 alternate reality 53 alternate universe 54 amazing cinematography 55 amazing photography 56 american civil war 57 amnesia 58 amy smart 59 android(s)/cyborg(s) 60 androids 61 animal movie 62 animals 63 animated 64 animation 65 anime 66 antarctica 67 anti-hero 68 anti-semitism 69 anti-war 70 apocalypse 71 archaeology 72 argentina 73 arms dealer 74 arnold 75 art 76 art house 77 artificial intelligence 78 artist 79 artistic 80 artsy 81 assassin 82 assassination 83 assassins 84 astronauts 85 atheism 86 atmospheric 87 australia 88 australian 89 author:alan moore 90 author:neil gaiman 91 autism 92 aviation 93 awesome 94 awesome soundtrack 95 awful 96 bad 97 bad acting 98 bad cgi 99 bad ending 100 bad plot 101 bad science 102 bad script 103 bad sequel 104 ballet 105 bank robbery 106 baseball 107 based on a book 108 based on a comic 109 based on a play 110 based on a true story 111 based on a tv show 112 based on a video game 113 based on book 114 based on comic 115 based on true story 116 basketball 117 batman 118 bdsm 119 beatles 120 beautiful 121 beautiful scenery 122 beautifully filmed 123 beauty pageant 124 beer 125 berlin 126 best of 2005 127 best war films 128 betrayal 129 better than expected 130 better than the american version 131 biblical 132 big budget 133 biographical 134 biography 135 biopic 136 birds 137 biting 138 bittersweet 139 bizarre 140 black and white 141 black comedy 142 blaxploitation 143 bleak 144 blindness 145 blood 146 bloody 147 boarding school 148 boat 149 bollywood 150 bombs 151 bond 152 book 153 book was better 154 books 155 boring 156 boring! 157 boston 158 bowling 159 boxing 160 brainwashing 161 brazil 162 breathtaking 163 brilliant 164 british 165 british comedy 166 broadway 167 brothers 168 brutal 169 brutality 170 buddy movie 171 bullshit history 172 bullying 173 business 174 c.s. lewis 175 california 176 camp 177 campy 178 canada 179 cancer 180 cannibalism 181 caper 182 capitalism 183 car chase 184 carrie-anne moss 185 cars 186 cartoon 187 casino 188 catastrophe 189 cathartic 190 catholicism 191 censorship 192 cerebral 193 cgi 194 character study 195 chase 196 cheating 197 cheerleading 198 cheesy 199 chess 200 chicago 201 chick flick 202 child abuse 203 childhood 204 children 205 china 206 chocolate 207 chris tucker 208 christian 209 christianity 210 christmas 211 cia 212 cinematography 213 circus 214 civil war 215 classic 216 classic car 217 classical music 218 claustrophobic 219 claymation 220 clever 221 clones 222 cloning 223 clowns 224 coen bros 225 coen brothers 226 cold war 227 college 228 colonialism 229 colourful 230 comedy 231 comic 232 comic book 233 comic book adaption 234 comics 235 coming of age 236 coming-of-age 237 communism 238 compassionate 239 competition 240 complex 241 complex characters 242 complicated 243 complicated plot 244 computer animation 245 computer game 246 computers 247 con artists 248 con men 249 confrontational 250 confusing 251 conspiracy 252 conspiracy theory 253 controversial 254 cooking 255 cool 256 corny 257 corporate america 258 corruption 259 costume drama 260 courage 261 court 262 courtroom 263 courtroom drama 264 crappy sequel 265 crazy 266 creativity 267 creepy 268 crime 269 crime gone awry 270 criterion 271 cross dressing 272 crude humor 273 cuba 274 cult 275 cult classic 276 cult film 277 cul

In [0]:
#Read data "Genome_scores"
ratings="/FileStore/tables/genome-scores.csv"
df_genome_scores= spark.read.format(file_type) \
      .option("inferSchema", infer_schema) \
      .option("header", first_row_is_header) \
      .option("sep", delimiter) \
      .load("abfss://data-storagetarget@sgmovielens.dfs.core.windows.net/genome-scores.csv")
    
display(df_genome_scores)

movieId tagId relevance 1 1 0.028749999999999998 1 2 0.023749999999999993 1 3 0.0625 1 4 0.07574999999999998 1 5 0.14075 1 6 0.14675 1 7 0.0635 1 8 0.20375 1 9 0.202 1 10 0.03075 1 11 0.58025 1 12 0.10249999999999998 1 13 0.20174999999999998 1 14 0.007000000000000006 1 15 0.024500000000000022 1 16 0.17275000000000001 1 17 0.016500000000000015 1 18 0.10399999999999998 1 19 0.6625 1 20 0.30074999999999996 1 21 0.31675 1 22 0.28600000000000003 1 23 0.06274999999999997 1 24 0.01924999999999999 1 25 0.058750000000000024 1 26 0.07924999999999999 1 27 0.1965 1 28 0.09325 1 29 0.89375 1 30 0.67625 1 31 0.035750000000000004 1 32 0.23325 1 33 0.3075 1 34 0.05449999999999999 1 35 0.03799999999999998 1 36 0.21200000000000002 1 37 0.08000000000000002 1 38 0.015500000000000014 1 39 0.019500000000000017 1 40 0.01924999999999999 1 41 0.015000000000000013 1 42 0.030000000000000027 1 43 0.09075 1 44 0.02250000000000002 1 45 0.246 1 46 0.246 1 47 0.01050000000000001 1 48 0.16675 1 49 0.2935 1 50 0.15000000000000002 1 51 0.26775000000000004 1 52 0.186 1 53 0.25725 1 54 0.15000000000000002 1 55 0.22049999999999997 1 56 0.014249999999999985 1 57 0.024249999999999994 1 58 0.029249999999999998 1 59 0.08424999999999999 1 60 0.03375 1 61 0.6175 1 62 0.63 1 63 0.9472499999999999 1 64 0.9842500000000001 1 65 0.09975 1 66 0.04149999999999998 1 67 0.135 1 68 0.033999999999999975 1 69 0.01824999999999999 1 70 0.14525 1 71 0.016749999999999987 1 72 0.018000000000000016 1 73 0.0595 1 74 0.009749999999999981 1 75 0.20124999999999998 1 76 0.016749999999999987 1 77 0.059250000000000025 1 78 0.03799999999999998 1 79 0.32925000000000004 1 80 0.028749999999999998 1 81 0.062 1 82 0.08700000000000002 1 83 0.035999999999999976 1 84 0.30474999999999997 1 85 0.068 1 86 0.33625000000000005 1 87 0.03649999999999998 1 88 0.005749999999999977 1 89 0.006749999999999978 1 90 0.05275000000000002 1 91 0.03325 1 92 0.02074999999999999 1 93 0.3435 1 94 0.36224999999999996 1 95 0.07400000000000001 1 96 0.06624999999999998 1 97 0.08174999999999999 1 98 0.064 1 99 0.12524999999999997 1 100 0.10549999999999998 1 101 0.05099999999999999 1 102 0.012249999999999983 1 103 0.007249999999999979 1 104 0.0040000000000000036 1 105 0.02350000000000002 1 106 0.005249999999999977 1 107 0.16349999999999998 1 108 0.038250000000000006 1 109 0.19524999999999998 1 110 0.07950000000000002 1 111 0.036250000000000004 1 112 0.019000000000000017 1 113 0.501 1 114 0.02174999999999999 1 115 0.1745 1 116 0.015749999999999986 1 117 0.005500000000000005 1 118 0.027000000000000024 1 119 0.0037499999999999756 1 120 0.1235 1 121 0.31225 1 122 0.23125 1 123 0.010000000000000009 1 124 0.046999999999999986 1 125 0.04275000000000001 1 126 0.08224999999999999 1 127 0.046999999999999986 1 128 0.368 1 129 0.23149999999999998 1 130 0.019000000000000017 1 131 0.016749999999999987 1 132 0.29325 1 133 0.08975 1 134 0.04475000000000001 1 135 0.05425000000000002 1 136 0.09475 1 137 0.06574999999999998 1 138 0.3295 1 139 0.028000000000000025 1 140 0.11525000000000002 1 141 0.11225000000000002 1 142 0.012249999999999983 1 143 0.16625 1 144 0.08574999999999999 1 145 0.07900000000000001 1 146 0.07324999999999998 1 147 0.02024999999999999 1 148 0.03175 1 149 0.08000000000000002 1 150 0.025500000000000023 1 151 0.04999999999999999 1 152 0.08074999999999999 1 153 0.046750000000000014 1 154 0.22925 1 155 0.05275000000000002 1 156 0.05375000000000002 1 157 0.03199999999999997 1 158 0.036250000000000004 1 159 0.02100000000000002 1 160 0.18525000000000003 1 161 0.018500000000000016 1 162 0.1835 1 163 0.08274999999999999 1 164 0.22099999999999997 1 165 0.057999999999999996 1 166 0.013249999999999984 1 167 0.1405 1 168 0.04199999999999998 1 169 0.22699999999999998 1 170 0.55075 1 171 0.11349999999999999 1 172 0.533 1 173 0.063 1 174 0.015749999999999986 1 175 0.1935 1 176 0.1395 1 177 0.04149999999999998 1 178 0.028749999999999998 1 179 0.060750000000000026 1 180 0.026500000000000024 1 181 0.04949999999999999 1 182 0.03475 1 183 0.0487500

In [0]:
df_movies.count()

Out[21]: 62423

In [0]:
#Join movies and ratings tables
df_movies_with_ratings = df_movies.join(df_ratings,'movieId','left')

display(df_movies_with_ratings)

movieId title genres userId rating timestamp 26 Othello (1995) Drama 34 3.0 1317760863 26 Othello (1995) Drama 90 3.0 863538343 26 Othello (1995) Drama 100 4.0 862168751 26 Othello (1995) Drama 179 4.0 849157930 26 Othello (1995) Drama 322 2.0 987392101 26 Othello (1995) Drama 325 4.0 868716756 26 Othello (1995) Drama 407 5.0 859254239 26 Othello (1995) Drama 576 5.0 843057851 26 Othello (1995) Drama 599 4.0 949272715 26 Othello (1995) Drama 621 3.0 875723591 26 Othello (1995) Drama 623 5.0 851880053 26 Othello (1995) Drama 726 5.0 869233856 26 Othello (1995) Drama 748 4.0 844683629 26 Othello (1995) Drama 766 5.0 839164145 26 Othello (1995) Drama 769 3.0 851183356 26 Othello (1995) Drama 801 2.5 1480454542 26 Othello (1995) Drama 811 5.0 829186422 26 Othello (1995) Drama 847 3.0 1109571521 26 Othello (1995) Drama 939 4.0 962590663 26 Othello (1995) Drama 986 2.0 863364768 26 Othello (1995) Drama 1089 4.0 1031599562 26 Othello (1995) Drama 1095 2.0 835219183 26 Othello (1995) Drama 1198 4.0 852606364 26 Othello (1995) Drama 1247 5.0 842871396 26 Othello (1995) Drama 1260 4.0 842907051 26 Othello (1995) Drama 1300 4.0 845586506 26 Othello (1995) Drama 1340 4.0 869324136 26 Othello (1995) Drama 1378 5.0 854195742 26 Othello (1995) Drama 1403 4.0 849599564 26 Othello (1995) Drama 1425 3.0 840015267 26 Othello (1995) Drama 1436 4.0 861372863 26 Othello (1995) Drama 1521 3.0 868828999 26 Othello (1995) Drama 1525 3.0 860937312 26 Othello (1995) Drama 1748 0.5 1425171677 26 Othello (1995) Drama 1832 3.0 877003535 26 Othello (1995) Drama 1833 3.0 1231043933 26 Othello (1995) Drama 1854 3.0 985620746 26 Othello (1995) Drama 1998 3.0 1462580947 26 Othello (1995) Drama 2082 4.0 865414822 26 Othello (1995) Drama 2177 3.0 882374049 26 Othello (1995) Drama 2317 3.0 940422562 26 Othello (1995) Drama 2383 4.0 855595533 26 Othello (1995) Drama 2496 3.0 1139229820 26 Othello (1995) Drama 2517 4.0 1135883044 26 Othello (1995) Drama 2543 3.0 856907796 26 Othello (1995) Drama 2545 4.0 828624879 26 Othello (1995) Drama 2590 3.0 868464054 26 Othello (1995) Drama 2649 4.0 989435156 26 Othello (1995) Drama 2658 3.0 1307135929 26 Othello (1995) Drama 2685 3.5 1118593354 26 Othello (1995) Drama 2714 5.0 857556283 26 Othello (1995) Drama 2801 4.0 852375205 26 Othello (1995) Drama 2803 3.0 875316795 26 Othello (1995) Drama 2887 5.0 967153738 26 Othello (1995) Drama 3204 1.0 855291517 26 Othello (1995) Drama 3225 3.0 1091273262 26 Othello (1995) Drama 3331 3.0 865065085 26 Othello (1995) Drama 3497 4.0 1073828622 26 Othello (1995) Drama 3551 4.0 879339246 26 Othello (1995) Drama 3561 4.0 848999264 26 Othello (1995) Drama 3574 4.0 844890687 26 Othello (1995) Drama 3623 4.0 1020782758 26 Othello (1995) Drama 3629 2.5 1111182835 26 Othello (1995) Drama 3728 5.0 886082035 26 Othello (1995) Drama 3746 5.0 866916104 26 Othello (1995) Drama 3779 3.0 845313018 26 Othello (1995) Drama 3849 5.0 861645562 26 Othello (1995) Drama 3957 4.0 918255280 26 Othello (1995) Drama 4100 2.0 839625153 26 Othello (1995) Drama 4103 1.0 852299443 26 Othello (1995) Drama 4133 3.0 859268394 26 Othello (1995) Drama 4145 4.0 1120277491 26 Othello (1995) Drama 4197 4.0 940533067 26 Othello (1995) Drama 4238 3.0 833046439 26 Othello (1995) Drama 4274 3.0 865260075 26 Othello (1995) Drama 4296 4.0 841219122 26 Othello (1995) Drama 4484 3.0 833686775 26 Othello (1995) Drama 4496 3.0 925832852 26 Othello (1995) Drama 4511 3.0 865449713 26 Othello (1995) Drama 4532 4.0 1077175058 26 Othello (1995) Drama 4540 3.0 842820989 26 Othello (1995) Drama 4568 4.0 846472922 26 Othello (1995) Drama 4651 5.0 865936762 26 Othello (1995) Drama 5056 2.0 1234822294 26 Othello (1995) Drama 5076 3.5 1205935726 26 Othello (1995) Drama 5095 3.0 845650794 26 Othello (1995) Drama 5101 3.0 850408332 26 Othello (1995) Drama 5177 5.0 874588030 26 Othello (1995) Drama 5268 4.0 857670009 26 Othello (1995) Drama 5333 5.0 868186181 26 Othello (1995) Drama 5349 4.0 1117817496 26 Othello (1995) Drama 5622 2.5 1197172976 

In [0]:
#Check if there are no duplicates
df_movies_no_dups = df_movies_with_ratings.groupby('movieId').count()
display(df_movies_no_dups)

movieId count 26 478 27 286 28 554 31 1787 34 6012 44 1999 53 26 65 850 76 608 78 194 81 492 85 450 101 829 108 19 115 9 126 246 133 3 137 39 148 48 155 231 159 389 183 114 192 12 193 1390 210 88 211 96 243 70 251 69 253 5381 255 176 271 209 296 15214 300 3547 321 160 322 529 332 382 362 1327 368 3128 375 37 384 145 385 19 392 50 406 13 412 794 436 232 451 99 458 167 463 63 471 2025 472 107 481 915 496 68 497 2477 501 331 513 96 516 631 530 6 540 849 577 129 580 100 587 5500 588 8215 593 14150 596 2385 597 6557 606 278 613 399 623 11 626 112 633 55 642 2 667 183 673 2032 683 6 688 543 723 6 731 139 737 783 743 1105 744 2 756 18 762 1731 772 6 784 2713 787 9 796 12 799 1125 804 385 806 81 808 147 830 1134 831 39 833 265 842 364 844 29 847 18 853 29 857 6 858 9879 874 10 876 51 879 383 897 142 898 1221 908 3237 914 1814 916 1173 918 351 939 33 950 619 961 47 970 76 974 28 976 66 988 97 1005 402 1016 248 1019 1073 1025 1100 1030 584 1031 790 1034 269 1051 217 1068 53 1084 1734 1088 2243 1127 3340 1133 17 1135 725 1139 4 1143 9 1148 2915 1156 12 1157 7 1160 6 1163 43 1165 4 1175 1372 1183 2808 1198 10332 1199 2901 1201 3448 1210 10404 1212 1364 1223 1481 1226 413 1235 1561 1238 587 1243 743 1259 4395 1265 7229 1269 1241 1270 9527 1274 1694 1276 2200 1280 579 1296 1183 1303 644 1307 4373 1322 50 1331 78 1339 1835 1342 680 1344 794 1350 1047 1352 121 1363 280 1372 1937 1378 1205 1395 388 1404 107 1415 40 1417 132 1426 38 1441 1066 1460 156 1466 2151 1468 208 1480 354 1483 500 1489 97 1493 40 1496 63 1500 2614 1507 66 1510 2 1522 4 1525 71 1533 57 1537 680 1561 7 1574 17 1580 7674 1591 1035 1621 124 1645 2638 1650 74 1653 4095 1675 17 1689 390 1699 220 1708 2 1718 10 1721 7161 1743 6 1752 300 1759 74 1771 60 1772 522 1787 3 1816 133 1826 80 1829 47 1863 165 1866 298 1869 78 1871 9 1875 205 1877 7 1884 1996 1888 532 1889 304 1892 854 1896 61 1903 6 1924 388 1927 472 1955 987 1959 948 1974 763 1975 328 1977 247 1990 30 2003 2224 2007 67 2015 446 2018 1480 2023 2044 2025 443 2027 196 2032 55 2035 62 2044 59 2047 36 2052 557 2076 1894 2079 30 2094 1230 2096 1353 2122 458 2134 1087 2142 424 2156 14 2169 201 2173 136 2180 112 2189 31 2200 19 2209 26 2212 222 2225 8 2231 1229 2235 7 2238 104 2240 293 2247 368 2249 314 2259 232 2261 204 2294 2118 2313 1384 2322 397 2331 223 2335 1257 2342 40 2349 268 2355 4281 2366 1181 2371 1187 2386 102 2387 426 2392 352 2393 1546 2396 4589 2439 294 2443 231 2463 563 2467 1033 2479 54 2484 3 2488 221 2513 673 2522 117 2525 142 2526 98 2542 3654 2559 91 2563 150 2564 4 2572 2629 2580 1513 2583 330 2601 3 2606 363 2610 53 2622 690 2625 110 2644 371 2650 34 2655 51 2656 57 2659 38 2662 893 2663 31 2678 32 2682 118 2683 4864 2697 61 2711 60 2721 124 2727 72 2738 96 2739 1026 2748 163 2750 391 2752 160 2754 10 2758 32 2771 282 2776 20 2778 28 2797 3960 2802 351 2804 2437 2809 54 2811 4 2821 5 2833 23 2835 78 2842 68 2848 79 2857 761 2866 239 2871 1530 2874 85 2888 240 2905 284 2907 303 2914 28 2923 29 2924 358 2945 13 2962 82 2971 413 2996 145 2999 11 3000 2472 3008 116 3010 65 3013 84 3017 124 3026 13 3028 154 3042 59 3043 37 3062 519 3069 51 3072 1326 3087 1018 3089 733 3098 854 3105 1392 3123 5 3124 20 3127 99 3133 38 3149 6 3151 1 3152 528 3166 16 3175 2844 3179 275 3183 39 3198 872 3211 70 3213 370 3220 7 3226 1 3234 1 3235 75 3242 5 3252 1751 3264 866 3270 299 3287 191 3296 311 3306 83 3313 23 3346 4 3352 3 3359 596 3370 53 3377 11 3387 207 3403 28 3411 1 3425 77 3431 87 3435 1025 3436 145 3441 519 3445 120 3475 150 3481 3247 3485 4 3488 9 3490 25 3528 322 3538 199 3561 1 3566 266 3577 45 3582 1 3587 52 3595 7 3601 6 3611 24 3624 1695 3626 58 3631 6 3650 6 3657 10 3666 16 3669 74 3685 399 3691 30 3698 1332 3703 1834 3704 1080 3706 532 3725 70 3727 221 3743 130 3744 782 3749 20 3761 96 3783 375 3790 53 3794 149 3795 39 3796 27 3811 320 3834 97 3841 308 3843 68 3844 592 3876 12 3885 33 3913 23 3918 248 3922 26 3936 101 3941 21 3986 1012 3997 398 4000 98 4036 432 4042 125 4061 198 4078 23 4083 26 4088 4 4092

In [0]:
#Join with users dataset
df_movies_with_ratings=df_movies_with_ratings.join(df_tags,['movieID','userId'],'inner')
display(df_movies_with_ratings)

movieId userId title genres rating timestamp tag timestamp 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 bright 1173304070 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 DARING RESCUES 1173304095 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 fanciful 1173304058 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 HEROIC MISSION 1173304102 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 humorous 1173304049 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 light 1173304062 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 rousing 1173304074 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 TOYS COME TO LIFE 1173304091 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 UNLIKELY FRIENDSHIPS 1173304106 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 warm 1173304052 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 witty 1173304077 1 21096 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.0 1049820315 Pixar 1244766522 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 animation 1528842677 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 classic 1528842699 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 clever 1528842702 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 comedy 1528842686 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 computer animation 1528842684 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 Disney 1528842680 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 friendship 1528842693 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 funny 1528842682 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 pixar 1528842674 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 witty 1528842691 2 6773 Jumanji (1995) Adventure|Children|Fantasy 2.0 1494850516 bad cgi 1494850524 2 6773 Jumanji (1995) Adventure|Children|Fantasy 2.0 1494850516 kid flick 1494850560 2 6773 Jumanji (1995) Adventure|Children|Fantasy 2.0 1494850516 scary 1494850566 2 6773 Jumanji (1995) Adventure|Children|Fantasy 2.0 1494850516 time travel 1494850530 2 20346 Jumanji (1995) Adventure|Children|Fantasy 3.0 1312089371 adapted from:book 1312089423 2 20346 Jumanji (1995) Adventure|Children|Fantasy 3.0 1312089371 childish 1312089444 2 20346 Jumanji (1995) Adventure|Children|Fantasy 3.0 1312089371 Children 1312089408 2 20346 Jumanji (1995) Adventure|Children|Fantasy 3.0 1312089371 kid flick 1312089388 2 20346 Jumanji (1995) Adventure|Children|Fantasy 3.0 1312089371 time travel 1312089401 3 13940 Grumpier Old Men (1995) Comedy|Romance 1.5 1139200225 sequel fever 1139200232 6 1048 Heat (1995) Action|Crime|Thriller 4.0 1328132907 imdb top 250 1172144427 6 3448 Heat (1995) Action|Crime|Thriller 3.5 1528815927 Al Pacino 1528913420 6 3448 Heat (1995) Action|Crime|Thriller 3.5 1528815927 atmospheric 1528913432 6 3448 Heat (1995) Action|Crime|Thriller 3.5 1528815927 bank robbery 1528913429 6 3448 Heat (1995) Action|Crime|Thriller 3.5 1528815927 crime 1528913425 6 3448 Heat (1995) Action|Crime|Thriller 3.5 1528815927 great acting 1528913424 6 3448 Heat (1995) Action|Crime|Thriller 3.5 1528815927 realistic action 1528913422 6 3448 Heat (1995) Action|Crime|Thriller 3.5 1528815927 Robert De Niro 1528913421 6 3448 Heat (1995) Action|Crime|Thriller 3.5 1528815927 suspense 1528913424 6 3448 Heat (1995) Action|Crime|Thriller 3.5 1528815927 tense 1528913427 6 3448

In [0]:
#Join with ratings with tag
df_ratings_tags=df_ratings.join(df_tags,['movieID'],'inner')
display(df_movies_with_ratings)

movieId userId title genres rating timestamp tag timestamp 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 bright 1173304070 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 DARING RESCUES 1173304095 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 fanciful 1173304058 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 HEROIC MISSION 1173304102 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 humorous 1173304049 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 light 1173304062 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 rousing 1173304074 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 TOYS COME TO LIFE 1173304091 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 UNLIKELY FRIENDSHIPS 1173304106 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 warm 1173304052 1 6285 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2.5 1195480693 witty 1173304077 1 21096 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.0 1049820315 Pixar 1244766522 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 animation 1528842677 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 classic 1528842699 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 clever 1528842702 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 comedy 1528842686 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 computer animation 1528842684 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 Disney 1528842680 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 friendship 1528842693 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 funny 1528842682 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 pixar 1528842674 1 28870 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 4.5 1528842666 witty 1528842691 2 6773 Jumanji (1995) Adventure|Children|Fantasy 2.0 1494850516 bad cgi 1494850524 2 6773 Jumanji (1995) Adventure|Children|Fantasy 2.0 1494850516 kid flick 1494850560 2 6773 Jumanji (1995) Adventure|Children|Fantasy 2.0 1494850516 scary 1494850566 2 6773 Jumanji (1995) Adventure|Children|Fantasy 2.0 1494850516 time travel 1494850530 2 20346 Jumanji (1995) Adventure|Children|Fantasy 3.0 1312089371 adapted from:book 1312089423 2 20346 Jumanji (1995) Adventure|Children|Fantasy 3.0 1312089371 childish 1312089444 2 20346 Jumanji (1995) Adventure|Children|Fantasy 3.0 1312089371 Children 1312089408 2 20346 Jumanji (1995) Adventure|Children|Fantasy 3.0 1312089371 kid flick 1312089388 2 20346 Jumanji (1995) Adventure|Children|Fantasy 3.0 1312089371 time travel 1312089401 3 13940 Grumpier Old Men (1995) Comedy|Romance 1.5 1139200225 sequel fever 1139200232 6 1048 Heat (1995) Action|Crime|Thriller 4.0 1328132907 imdb top 250 1172144427 6 3448 Heat (1995) Action|Crime|Thriller 3.5 1528815927 Al Pacino 1528913420 6 3448 Heat (1995) Action|Crime|Thriller 3.5 1528815927 atmospheric 1528913432 6 3448 Heat (1995) Action|Crime|Thriller 3.5 1528815927 bank robbery 1528913429 6 3448 Heat (1995) Action|Crime|Thriller 3.5 1528815927 crime 1528913425 6 3448 Heat (1995) Action|Crime|Thriller 3.5 1528815927 great acting 1528913424 6 3448 Heat (1995) Action|Crime|Thriller 3.5 1528815927 realistic action 1528913422 6 3448 Heat (1995) Action|Crime|Thriller 3.5 1528815927 Robert De Niro 1528913421 6 3448 Heat (1995) Action|Crime|Thriller 3.5 1528815927 suspense 1528913424 6 3448 Heat (1995) Action|Crime|Thriller 3.5 1528815927 tense 1528913427 6 3448

In [0]:
#Converting timestamp to readable format.
#int to string
df_ratings=df_ratings.withColumn("tsDate",f.from_unixtime("timestamp"))

In [0]:
#String to date conversion 
df_ratings=df_ratings.select('userId','movieId','rating',f.to_date(unix_timestamp('tsDate', 'yyyy-MM-dd HH:MM:SS').cast('timestamp')).alias('rating_date'))

In [0]:
spark.sql("set spark.sql.legacy.timeParserPolicy=LEGACY")
df_ratings_year=df_ratings.groupBy('rating_date').count()
display(df_ratings_year)

rating_date count 2006-05-17 137 2015-05-19 155 1997-02-08 53 1998-05-16 37 1996-12-22 171 2000-12-26 140 2010-08-11 96 2017-09-11 116 2017-08-11 122 1999-08-14 134 2000-03-17 122 2005-06-06 88 2014-09-26 27 2016-03-01 240 2018-05-28 173 2002-06-20 88 2013-01-22 66 2006-05-21 91 2012-10-06 42 2013-09-09 55 2007-11-15 108 2000-07-03 177 2002-03-02 129 1997-12-11 87 2018-08-10 157 2002-12-06 81 1999-02-01 124 2019-05-08 125 2007-04-20 80 2012-04-17 90 2013-03-26 63 2013-05-21 48 2002-12-25 60 2015-03-09 167 2009-11-22 84 2019-06-04 78 2009-07-25 58 2001-05-16 97 2007-11-23 80 2005-01-16 119 2014-11-12 41 2019-11-18 93 1997-09-17 91 2001-06-27 76 1997-08-08 43 2018-03-17 125 2009-08-09 64 2010-09-24 110 2011-01-30 59 1998-08-24 38 2011-05-06 32 2009-09-27 71 1999-04-22 120 2017-01-06 153 2015-03-06 139 2016-04-25 172 2003-11-11 99 1999-11-19 160 2009-06-28 78 2002-01-23 58 2008-09-26 107 2011-10-07 71 2000-12-25 176 1996-03-09 159 2007-04-19 110 2002-11-15 122 2000-11-19 241 2009-10-19 125 2008-07-15 80 1997-01-18 52 2012-07-17 76 1998-01-04 29 2019-09-22 60 2004-07-27 121 2004-10-24 106 2004-02-23 122 2018-06-06 110 2004-07-12 107 2006-04-23 68 2019-11-01 70 2013-09-19 47 2011-01-29 46 1996-01-22 187 2005-08-14 146 2007-03-29 42 2018-06-26 81 2001-11-13 73 2013-02-02 51 2011-11-18 47 2014-08-01 32 2016-07-26 236 2018-09-01 127 2003-12-07 120 2015-12-22 178 2012-11-11 70 2005-10-04 147 2006-02-28 101 2010-04-15 73 1999-04-27 93 2009-03-21 84 2002-04-23 74 2011-07-07 63 2016-08-31 58 2007-05-15 89 2006-12-01 64 2005-08-03 203 2018-10-05 142 2018-09-09 126 2007-12-28 118 1996-03-03 146 2011-01-23 78 2009-05-13 84 2018-08-08 149 2002-09-06 103 1999-07-26 73 2019-11-21 99 2018-08-11 144 2016-05-03 135 2015-04-09 151 2009-06-25 70 2015-09-02 177 2018-11-02 105 2010-08-16 58 2008-02-01 96 1999-09-28 56 2016-08-15 130 2009-02-14 100 2001-03-12 122 2000-03-09 158 2011-08-21 52 2016-10-03 185 2011-07-18 28 2003-03-28 75 1997-03-26 43 1999-06-03 150 2014-06-03 28 2010-07-19 88 2016-01-28 222 2008-01-20 83 2012-08-23 37 2000-07-08 169 1998-08-30 16 2017-02-26 165 2010-12-15 101 2006-11-13 109 2017-09-28 142 2006-12-26 140 2012-09-21 66 2012-02-12 88 2017-01-27 172 2019-05-27 74 1999-06-26 63 2002-01-26 91 2006-02-09 151 2003-11-10 71 2009-03-12 71 2001-11-04 123 2018-06-30 207 2003-08-28 99 2008-02-07 86 2010-05-23 66 2010-12-01 120 2003-09-27 125 2006-06-30 74 2017-01-24 167 2010-06-19 100 2019-02-23 106 2002-08-29 51 1997-06-20 53 2018-11-01 133 2002-02-27 67 2003-06-07 144 2014-02-16 46 2006-09-07 119 2003-07-16 104 2016-07-17 178 1999-07-16 121 2001-07-17 124 2007-09-09 82 2007-10-09 70 2014-06-11 32 2004-07-08 85 1999-09-06 65 2006-03-18 73 2016-11-08 130 2010-04-14 49 2001-01-30 130 2015-05-10 114 2008-02-14 119 1996-04-11 121 2010-02-20 73 2006-12-22 92 2016-12-19 187 2013-02-04 54 1999-08-12 172 2011-11-14 64 2003-08-20 54 2015-09-28 152 1996-05-31 102 2013-09-12 60 2012-07-14 60 2001-06-09 114 1999-02-10 53 1996-10-06 188 2014-01-24 46 1998-10-28 14 1998-06-18 34 2010-06-10 57 1998-12-07 33 2011-09-04 86 2015-03-16 171 2010-08-25 118 1996-06-28 87 1999-01-06 53 2003-05-12 78 2012-09-11 70 2015-04-01 133 2006-12-18 102 2010-09-22 96 1997-02-22 84 2016-08-23 112 2017-09-29 176 2000-10-13 102 2017-06-29 147 2011-06-21 42 2000-07-05 192 2008-04-28 117 1999-07-14 154 2009-05-01 89 2009-08-02 62 2015-03-12 152 2016-07-03 157 2006-11-16 122 2012-11-03 51 2013-11-18 40 2015-04-24 146 2008-09-02 114 2011-02-21 49 1997-08-17 110 1996-03-20 166 2012-05-02 26 2003-06-04 86 2014-08-13 64 2003-07-31 62 2008-06-24 54 2011-04-06 35 2004-10-03 102 2014-02-18 32 1998-07-09 30 1998-02-07 28 2003-07-27 142 1999-01-20 89 2009-02-09 84 2018-05-26 112 2015-10-16 159 2000-11-26 149 2004-10-26 118 2019-01-08 165 1999-01-14 200 2014-07-06 77 2013-10-05 62 2012-09-01 75 2013-03-17 83 2009-01-01 83 2001-03-21 103 2004-04-22 116 2001-05-17 124 2009-08-21 81 2001-06-14 123 2001-08-16 133 2011-08-30 82 2015-03-11 101 2018-03-23 136 2017-07-31 134 1996-08-13 189 

In [0]:
df_avg_rating = df_ratings.groupBy('movieId').mean('rating')
display(df_avg_rating)

movieId avg(rating) 1088 3.256130182790905 1580 3.5884805837894187 3175 3.6235935302391 44022 3.217750257997936 175197 2.654471544715447 1645 3.5489006823351024 471 3.65358024691358 3794 3.271812080536913 8638 3.969664138678223 33722 3.7142857142857144 2142 3.035377358490566 2366 3.5317527519051652 6658 2.9484126984126986 1959 3.6281645569620253 6620 3.7616959064327484 54190 3.6039260969976907 3918 2.913306451612903 68135 3.072407045009785 1342 2.9691176470588236 1591 2.6159420289855073 2122 2.6080786026200875 3997 2.0766331658291457 96488 3.965909090909091 31528 3.675 32460 4.053333333333334 833 2.630188679245283 4519 3.341541755888651 4900 3.1120689655172415 1238 4.021294718909711 2866 3.6820083682008367 5803 2.7389558232931726 7340 2.9642857142857144 463 2.873015873015873 36525 3.5 97186 3.35 6357 3.6538461538461537 3749 3.375 7982 3.4907975460122698 5518 4.090909090909091 7833 3.772727272727273 5300 3.5841121495327104 179749 3.2906976744186047 141422 3.511627906976744 27760 3.7857142857142856 31367 2.9347826086956523 82529 2.625 96853 3.0 139747 3.6097560975609757 144414 3.5 144522 3.5 6466 3.5076923076923077 160563 3.1333333333333333 7240 2.95 64519 3.6666666666666665 7993 3.225 26425 3.9166666666666665 27484 3.25 58061 4.0 119432 3.75 180981 3.5 204780 4.0 166558 3.3088235294117645 496 3.573529411764706 148 2.8020833333333335 180191 3.0 1829 2.904255319148936 26755 3.3333333333333335 142084 3.7083333333333335 31035 3.8484848484848486 135867 3.5833333333333335 149761 2.75 31983 3.5 57370 2.6774193548387095 172523 2.6 6654 3.2 150604 3.1333333333333333 91937 3.3 7253 3.5 76143 3.625 40574 2.8378378378378377 41575 3.1153846153846154 189149 2.5 47084 3.857142857142857 150375 4.0 63645 4.375 145504 3.25 6336 3.2 173691 2.5 179115 3.625 104064 2.75 141299 3.5 109613 3.5 175229 3.0 188125 3.2 26708 1.0 143432 1.5 80451 1.75 176073 2.8333333333333335 185513 3.0 168654 3.625 179217 1.0 124861 3.1666666666666665 4935 3.4166666666666665 116259 4.0 193137 3.125 206351 1.0 2659 3.3947368421052633 4818 2.0 5156 3.142857142857143 139335 3.0 135965 2.25 134607 5.0 133153 3.75 858 4.3299929142625775 1127 3.6589820359281435 48780 4.096106234526221 69481 3.736666666666667 166635 3.56629392971246 1721 3.3928920541823766 540 2.751472320376914 1084 3.855824682814302 1025 3.5072727272727273 1522 2.5 2580 3.643423661599471 6773 3.8504098360655736 3698 3.2394894894894897 4161 2.983031674208145 2387 2.801643192488263 1395 3.4188144329896906 737 2.079182630906769 243 2.7071428571428573 1483 3.1 1507 3.5833333333333335 1460 2.496794871794872 2563 3.6 4219 3.208791208791209 56941 3.450854700854701 101362 3.181967213114754 110433 2.7857142857142856 4158 2.1306818181818183 43921 3.5365853658536586 101971 3.8823529411764706 51927 2.9144144144144146 392 3.52 897 3.658450704225352 96565 2.830188679245283 133255 2.6666666666666665 3179 3.5309090909090908 1896 3.2950819672131146 4190 3.9363636363636365 196889 3.2327586206896552 92008 3.0885416666666665 623 3.272727272727273 74452 2.7227272727272727 146018 3.375 147246 3.0833333333333335 45183 3.5 50954 3.1 81312 2.0 96415 3.0 99996 3.409090909090909 101761 2.816666666666667 103547 1.8888888888888888 111447 1.625 116947 3.25 119169 2.3333333333333335 165287 3.8333333333333335 78905 3.7 1990 1.35 8928 3.3197674418604652 48711 3.4047619047619047 2235 1.8571428571428572 3475 3.94 26699 3.966666666666667 47935 3.25 7417 2.5714285714285716 182637 3.759259259259259 6623 2.111111111111111 177771 2.9833333333333334 91690 2.9913793103448274 8932 2.86 65300 2.3636363636363638 185435 2.4642857142857144 63781 3.25 4929 2.625 8803 3.2916666666666665 186173 3.0 152061 3.140625 93037 3.0 7168 2.9615384615384617 27888 2.4615384615384617 62526 2.8 158673 1.75 3226 5.0 152836 2.5 163663 3.466666666666667 178895 2.5 65974 2.75 166445 3.75 46108 4.5 182387 3.6 191479 3.1153846153846154 202237 3.5 41704 2.357142857142857 184073 2.0 27261 3.4375 158300 3.8333333333333335 151791 3.8333333333333335 176339 2.8333333333333335 2999 3

In [0]:
df=df_avg_rating.join(df_movies,'movieId', 'inner')
df=df.withColumnRenamed('avg(rating)','avg_rating')
display(df)

movieId avg_rating title genres 1088 3.256130182790905 Dirty Dancing (1987) Drama|Musical|Romance 1580 3.5884805837894187 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 3175 3.6235935302391 Galaxy Quest (1999) Adventure|Comedy|Sci-Fi 44022 3.217750257997936 Ice Age 2: The Meltdown (2006) Adventure|Animation|Children|Comedy 175197 2.654471544715447 The Dark Tower (2017) Fantasy|Horror|Sci-Fi|Western 1645 3.5489006823351024 The Devil's Advocate (1997) Drama|Mystery|Thriller 471 3.65358024691358 Hudsucker Proxy, The (1994) Comedy 3794 3.271812080536913 Chuck & Buck (2000) Comedy|Drama 8638 3.969664138678223 Before Sunset (2004) Drama|Romance 33722 3.7142857142857144 Ladies in Lavender (2004) Comedy|Drama|Romance 2142 3.035377358490566 American Tail: Fievel Goes West, An (1991) Adventure|Animation|Children|Musical|Western 2366 3.5317527519051652 King Kong (1933) Action|Adventure|Fantasy|Horror 6658 2.9484126984126986 10 (1979) Comedy|Romance 1959 3.6281645569620253 Out of Africa (1985) Drama|Romance 6620 3.7616959064327484 American Splendor (2003) Comedy|Drama 54190 3.6039260969976907 Across the Universe (2007) Drama|Fantasy|Musical|Romance 3918 2.913306451612903 Hellbound: Hellraiser II (1988) Horror 68135 3.072407045009785 17 Again (2009) Comedy|Drama 1342 2.9691176470588236 Candyman (1992) Horror|Thriller 1591 2.6159420289855073 Spawn (1997) Action|Adventure|Sci-Fi|Thriller 2122 2.6080786026200875 Children of the Corn (1984) Horror|Thriller 3997 2.0766331658291457 Dungeons & Dragons (2000) Action|Adventure|Comedy|Fantasy 96488 3.965909090909091 Searching for Sugar Man (2012) Documentary 31528 3.675 Beau Geste (1939) Action|Adventure|Drama|War 32460 4.053333333333334 Knockin' on Heaven's Door (1997) Action|Comedy|Crime|Drama 833 2.630188679245283 High School High (1996) Comedy 4519 3.341541755888651 Land Before Time, The (1988) Adventure|Animation|Children|Fantasy 4900 3.1120689655172415 Out Cold (2001) Comedy 1238 4.021294718909711 Local Hero (1983) Comedy 2866 3.6820083682008367 Buddy Holly Story, The (1978) Drama 5803 2.7389558232931726 I Spy (2002) Action|Adventure|Comedy|Crime 7340 2.9642857142857144 Just One of the Guys (1985) Comedy 463 2.873015873015873 Guilty as Sin (1993) Crime|Drama|Thriller 36525 3.5 Just Like Heaven (2005) Comedy|Fantasy|Romance 97186 3.35 Sinivalkoinen valhe (2012) Documentary 6357 3.6538461538461537 High Society (1956) Comedy|Musical|Romance 3749 3.375 Time Regained (Temps retrouvé, Le) (1999) Drama 7982 3.4907975460122698 Tale of Two Sisters, A (Janghwa, Hongryeon) (2003) Drama|Horror|Mystery|Thriller 5518 4.090909090909091 Beau Pere (a.k.a. Stepfather) (Beau-père) (1981) Drama 7833 3.772727272727273 Shadow of the Thin Man (1941) Comedy|Crime|Mystery 5300 3.5841121495327104 3:10 to Yuma (1957) Action|Adventure|Drama|Thriller|Western 179749 3.2906976744186047 Creep 2 (2017) Comedy|Horror 141422 3.511627906976744 Suffragette (2015) Drama 27760 3.7857142857142856 When the Last Sword is Drawn (Mibu gishi den) (2003) Drama 31367 2.9347826086956523 Chase, The (1994) Action|Adventure|Comedy|Crime|Romance|Thriller 82529 2.625 Soo (Art of Revenge) (2007) Action|Crime|Drama|Thriller 96853 3.0 Thin Ice (2011) Comedy|Crime|Drama 139747 3.6097560975609757 Before We Go (2014) Romance 144414 3.5 Seven Days (2007) Crime 144522 3.5 Sky High (2003) Action|Horror|Thriller 6466 3.5076923076923077 Mississippi Masala (1991) Drama|Romance 160563 3.1333333333333333 The Legend of Tarzan (2016) Action|Adventure 7240 2.95 King David (1985) Action|Drama|War 64519 3.6666666666666665 Boomerang (1947) Crime|Drama|Film-Noir 7993 3.225 Bucket Of Blood, A (1959) Comedy|Horror 26425 3.9166666666666665 In-Laws, The (1979) Action|Comedy 27484 3.25 Milwaukee, Minnesota (2003) Drama 58061 4.0 Four Sons (1928) Drama 119432 3.75 A Thousand Times Goodnight (2014) Drama 180981 3.5 Look & See: A Portrait of Wendell Berry (2017) Documentary 204780 4.0 Voilà l'enchaînement (2014) Drama 166558 3.3088235294117645 Underworld: Blood Wars 

In [0]:
df_total_rating=df_ratings.groupBy('movieId').count()
display(df_total_rating)

movieId count 1088 2243 1580 7674 3175 2844 44022 969 175197 123 1645 2638 471 2025 3794 149 8638 923 33722 35 2142 424 2366 1181 6658 126 1959 948 6620 684 54190 433 3918 248 68135 511 1342 680 1591 1035 2122 458 3997 398 96488 264 31528 40 32460 150 833 265 4519 467 4900 58 1238 587 2866 239 5803 249 7340 56 463 63 36525 383 97186 10 6357 91 3749 20 7982 163 5518 11 7833 55 5300 107 179749 43 141422 43 27760 7 31367 46 82529 4 96853 4 139747 41 144414 3 144522 3 6466 65 160563 135 7240 10 64519 9 7993 20 26425 60 27484 2 58061 2 119432 4 180981 1 204780 1 166558 102 496 68 148 48 180191 1 1829 47 26755 9 142084 12 31035 33 135867 12 149761 2 31983 15 57370 31 172523 5 6654 5 150604 15 91937 5 7253 14 76143 8 40574 37 41575 13 189149 4 47084 7 150375 1 63645 4 145504 2 6336 5 173691 1 179115 4 104064 2 141299 3 109613 1 175229 1 188125 5 26708 1 143432 2 80451 2 176073 3 185513 1 168654 4 179217 1 124861 3 4935 6 116259 1 193137 4 206351 1 2659 38 4818 11 5156 7 139335 1 135965 2 134607 1 133153 2 858 9879 1127 3340 48780 4443 69481 1500 166635 626 1721 7161 540 849 1084 1734 1025 1100 1522 4 2580 1513 6773 732 3698 1332 4161 884 2387 426 1395 388 737 783 243 70 1483 500 1507 66 1460 156 2563 150 4219 91 56941 468 101362 305 110433 7 4158 176 43921 164 101971 17 51927 111 392 50 897 142 96565 53 133255 3 3179 275 1896 61 4190 110 196889 116 92008 96 623 11 74452 110 146018 8 147246 12 45183 92 50954 60 81312 7 96415 8 99996 22 101761 30 103547 9 111447 4 116947 4 119169 3 165287 3 78905 5 1990 30 8928 86 48711 21 2235 7 3475 150 26699 30 47935 6 7417 21 182637 27 6623 9 177771 30 91690 58 8932 25 65300 11 185435 14 63781 2 4929 124 8803 12 186173 1 152061 64 93037 2 7168 13 27888 13 62526 5 158673 2 3226 1 152836 5 163663 15 178895 2 65974 6 166445 2 46108 3 182387 5 191479 13 202237 8 41704 7 184073 1 27261 8 158300 3 151791 3 176339 3 2999 11 149178 3 31680 2 200448 8 26544 6 57513 3 206135 1 105252 3 130912 1 190509 2 119907 3 199478 2 176351 6 180445 1 5614 16 131389 14 136660 2 27266 258 1270 9527 6482 364 516 631 1322 50 2572 2629 31 1787 1339 1835 2393 1546 31435 66 3000 2472 55363 499 82459 1400 93240 29 3213 370 50792 88 4489 1057 1303 644 1352 121 80906 416 26111 72 176751 170 3704 1080 1699 220 6266 269 5117 44 7387 677 71670 69 74948 162 87028 29 2996 145 80315 6 5071 28 41126 2 53741 4 55272 123 71732 23 114680 9 135137 189 142608 5 6559 89 6825 14 34488 4 3488 9 7281 13 61250 165 5287 33 5984 32 4391 30 32525 39 96706 1 191869 28 1139 4 1143 9 188477 7 1903 6 189819 17 1650 74 32560 8 174181 11 40578 4 196417 82 2776 20 3761 96 183077 10 85268 20 26178 29 93432 29 7879 37 8407 8 26128 12 8222 25 197207 15 8924 18 34435 23 86206 6 67865 2 67068 13 55498 16 186045 5 79760 12 184215 1 173151 2 163118 7 56022 5 38656 16 54958 8 149344 3 150554 2 186607 1 7850 2 8257 16 94283 1 109450 4 181689 2 103751 3 188603 2 48035 10 58850 11 153674 1 5345 3 2711 60 136030 9 135846 2 135520 3 131506 8 5173 6 3098 854 3986 1012 33615 1331 83613 473 1265 7229 1884 1996 3089 733 32291 112 26375 117 116905 37 136906 3 2025 443 2231 1229 4239 1672 808 147 85 450 33437 277 4042 125 451 99 5308 614 76293 418 101088 159 2748 163 75341 145 5074 176 91653 226 2259 232 192389 218 6598 56 51086 542 71106 153 71571 29 2443 231 151367 1 1975 328 2488 221 178667 82 113829 111 94967 16 4186 66 5223 26 580 100 44653 22 2525 142 4078 23 251 69 4364 2 27255 20 49668 3 89900 46 193697 14 100942 2 8911 72 137 39 27856 16 31689 51 5482 43 2721 124 31290 9 26736 28 156187 1 8779 17 110871 3 3490 25 159704 1 56490 4 111680 7 5155 17 3796 27 8650 29 56350 13 172389 1 4937 12 73900 10 2923 29 7066 21 6597 23 8743 7 157775 2 162354 1 149090 5 74681 2 104224 3 172255 15 180359 1 44595 7 123553 3 147895 2 130580 9 104610 1 90873 8 107002 4 31447 3 125599 2 79207 6 193916 11 34450 3 113236 1 7120 7 110505 1 104829 6 128556 1 43260 4 144146 1 199864 2 203886 1 3876 12 126036 2 4684 7 135260 2 134800 3 134623 1 131964 3 139533 1 156898 3 8665 3803 4383 206 693

In [0]:
# Filter movies which has been rated less than 30 times
df_total_rating=df_total_rating.filter(df_total_rating['count']>30)
df_ratings_filtered=df_ratings.join(df_total_rating,'movieId','inner')
display(df_ratings_filtered)

movieId userId rating rating_date count 1088 1 4.0 null 2243 1580 2 4.5 null 7674 3175 2 3.5 null 2844 44022 3 4.0 null 969 175197 3 3.5 null 123 1580 4 4.5 2019-02-16 7674 3175 4 4.0 null 2844 1580 8 5.0 1998-07-21 7674 1645 8 4.0 1998-09-21 2638 1088 9 5.0 null 2243 471 12 4.0 null 2025 1088 12 4.0 null 2243 1580 12 3.5 null 7674 3794 12 2.0 null 149 8638 12 4.0 null 923 33722 12 3.0 2006-04-02 35 1580 13 3.5 null 7674 2142 13 4.5 null 424 2366 13 3.5 null 1181 3175 13 4.0 2010-07-06 2844 1088 15 2.0 null 2243 1580 15 4.0 1999-11-24 7674 1580 18 4.0 null 7674 1580 20 4.0 2006-12-09 7674 6658 20 2.0 null 126 1959 23 5.0 null 948 1580 28 5.0 null 7674 1580 30 5.0 null 7674 3175 30 4.5 null 2844 1580 31 3.0 null 7674 3175 31 1.5 null 2844 6620 31 1.5 null 684 8638 31 2.0 null 923 1088 40 2.5 null 2243 1580 41 4.0 null 7674 2366 41 3.0 1999-06-07 1181 1580 43 4.0 null 7674 3175 43 3.5 2007-10-03 2844 8638 43 4.0 null 923 44022 43 3.0 null 969 1088 50 4.0 null 2243 1645 50 5.0 null 2638 1580 56 5.0 null 7674 1580 57 3.0 null 7674 6658 58 5.0 2012-06-16 126 54190 58 5.0 null 433 471 59 3.5 2005-06-22 2025 1580 59 3.5 null 7674 3175 59 4.0 null 2844 3918 59 3.0 null 248 1088 61 4.0 null 2243 1580 61 4.0 null 7674 1959 61 3.0 null 948 3175 61 4.0 2001-11-07 2844 68135 63 4.0 null 511 1580 67 4.0 null 7674 2142 67 2.0 2000-11-01 424 1580 69 0.5 null 7674 1580 70 3.0 null 7674 1959 70 4.0 null 948 6658 70 3.0 null 126 471 72 5.0 null 2025 1088 72 4.0 null 2243 1342 72 4.0 null 680 1580 72 4.0 null 7674 1591 72 2.0 null 1035 1645 72 4.0 null 2638 2122 72 2.0 null 458 3175 72 3.0 null 2844 3918 72 3.0 null 248 1088 75 3.5 null 2243 1959 75 2.0 null 948 8638 75 3.0 2018-07-17 923 1342 76 3.5 null 680 1959 76 5.0 null 948 3175 76 3.5 null 2844 1342 80 2.0 null 680 1580 80 3.0 null 7674 1591 80 2.0 null 1035 1645 80 5.0 null 2638 3997 80 1.0 2001-12-22 398 6620 82 3.0 null 684 96488 82 4.0 null 264 1580 83 3.5 null 7674 471 84 3.5 null 2025 96488 84 4.0 null 264 1088 85 2.0 null 2243 1580 86 4.0 1999-11-17 7674 3175 87 4.5 null 2844 1088 89 3.5 null 2243 1580 89 3.0 null 7674 1645 89 3.5 null 2638 8638 91 3.0 null 923 96488 91 2.0 null 264 44022 93 4.0 null 969 1088 98 4.0 null 2243 68135 98 4.5 null 511 8638 101 5.0 2015-04-21 923 2142 102 3.0 null 424 6658 102 4.0 null 126 31528 102 4.0 2009-04-09 40 54190 102 5.0 null 433 471 107 3.0 null 2025 6620 107 3.0 null 684 8638 107 3.0 null 923 8638 109 4.0 2019-02-17 923 32460 109 4.0 2019-02-17 150 1580 111 4.0 2006-12-27 7674 471 113 4.0 null 2025 44022 114 3.5 2019-03-03 969 1580 116 3.0 null 7674 1088 117 4.0 2015-06-05 2243 54190 119 1.0 null 433 68135 119 2.5 null 511 1088 120 4.0 null 2243 1580 120 5.0 null 7674 3175 120 4.0 null 2844 1580 123 4.0 null 7674 1591 123 3.0 null 1035 471 124 4.0 null 2025 833 125 3.0 null 265 1088 125 2.0 null 2243 1580 125 5.0 null 7674 4519 125 3.0 2002-03-01 467 4900 125 4.0 null 58 96488 127 5.0 null 264 1238 132 5.0 null 587 1580 132 3.0 2002-09-17 7674 1959 132 4.0 null 948 471 133 4.0 null 2025 1645 137 3.0 null 2638 54190 138 3.5 null 433 68135 138 0.5 2011-10-01 511 1580 142 3.0 null 7674 1580 144 3.0 null 7674 2366 144 2.0 null 1181 8638 144 3.5 null 923 33722 144 3.5 null 35 3175 147 3.0 null 2844 1580 155 2.5 null 7674 1580 156 4.0 null 7674 471 158 5.0 null 2025 54190 159 5.0 null 433 1580 160 4.5 2007-05-16 7674 1580 163 3.5 null 7674 8638 164 4.0 null 923 1088 166 5.0 null 2243 1238 166 2.0 null 587 1580 166 4.0 null 7674 1959 166 3.0 null 948 2866 166 3.0 null 239 1088 169 3.5 2008-05-20 2243 54190 169 3.5 2008-04-20 433 68135 169 3.5 2009-09-29 511 471 171 4.0 null 2025 1580 171 4.5 null 7674 1645 171 4.5 2004-10-20 2638 3175 171 3.5 null 2844 5803 171 4.0 null 249 1088 172 5.0 null 2243 8638 172 4.0 2015-06-29 923 1088 175 4.0 null 2243 1580 175 4.0 null 7674 1959 175 2.0 2001-08-13 948 2866 175 4.0 null 239 3175 175 3.0 null 2844 471 176 4.0 null 2025 1580 177 3.0 null 7674 3175 178 3.0 null 2844 1342 181 2.5 null 680 1580 181 1.5 null 76

In [0]:
#Data Preperation for further analysis
df_ratings_filtered.count()

Out[76]: 4610081

In [0]:
df_rating_per_user= df_ratings_filtered.select('userId','movieId','rating').groupBy('userId','movieId').max('rating')
df_rating_per_user_movies=df_rating_per_user.join(df_movies,'movieId','inner')
df_rating_per_user_movies=df_rating_per_user_movies.withColumnRenamed('max(rating)','max_rating')


movieId userId max_rating title genres 1892 2394 4.5 Perfect Murder, A (1998) Thriller 1175 2395 4.5 Delicatessen (1991) Comedy|Drama|Romance 1201 2397 4.0 Good, the Bad and the Ugly, The (Buono, il brutto, il cattivo, Il) (1966) Action|Adventure|Western 2313 2400 4.0 Elephant Man, The (1980) Drama 57274 2400 4.0 [REC] (2007) Drama|Horror|Thriller 2683 2403 3.5 Austin Powers: The Spy Who Shagged Me (1999) Action|Adventure|Comedy 7325 2403 3.5 Starsky & Hutch (2004) Action|Comedy|Crime|Thriller 7460 2403 2.5 Coffee and Cigarettes (2003) Comedy|Drama 34164 2403 3.5 Happy Endings (2005) Comedy|Drama 436 2404 1.0 Color of Night (1994) Drama|Thriller 2463 2404 4.0 Ruthless People (1986) Comedy 2683 2406 0.5 Austin Powers: The Spy Who Shagged Me (1999) Action|Adventure|Comedy 7325 2406 0.5 Starsky & Hutch (2004) Action|Comedy|Crime|Thriller 44193 2406 4.0 She's the Man (2006) Comedy|Romance 80166 2406 3.5 Switch, The (2010) Comedy|Romance 28 2413 3.0 Persuasion (1995) Drama|Romance 1441 2413 3.0 Benny & Joon (1993) Comedy|Romance 2683 2414 4.0 Austin Powers: The Spy Who Shagged Me (1999) Action|Adventure|Comedy 31162 2415 3.5 Life and Death of Peter Sellers, The (2004) Comedy|Drama 2052 2418 4.0 Hocus Pocus (1993) Children|Comedy|Fantasy|Horror 4958 2418 4.0 Behind Enemy Lines (2001) Action|Drama|War 1175 2419 4.0 Delicatessen (1991) Comedy|Drama|Romance 1201 2419 3.5 Good, the Bad and the Ugly, The (Buono, il brutto, il cattivo, Il) (1966) Action|Adventure|Western 2683 2419 1.5 Austin Powers: The Spy Who Shagged Me (1999) Action|Adventure|Comedy 4326 2419 3.5 Mississippi Burning (1988) Crime|Drama|Thriller 1201 2424 5.0 Good, the Bad and the Ugly, The (Buono, il brutto, il cattivo, Il) (1966) Action|Adventure|Western 1892 2424 4.0 Perfect Murder, A (1998) Thriller 1175 2427 4.0 Delicatessen (1991) Comedy|Drama|Romance 5152 2428 4.0 We Were Soldiers (2002) Action|Drama|War 1201 2429 4.0 Good, the Bad and the Ugly, The (Buono, il brutto, il cattivo, Il) (1966) Action|Adventure|Western 2683 2429 2.0 Austin Powers: The Spy Who Shagged Me (1999) Action|Adventure|Comedy 4326 2429 3.5 Mississippi Burning (1988) Crime|Drama|Thriller 57274 2429 4.0 [REC] (2007) Drama|Horror|Thriller 2683 2430 3.5 Austin Powers: The Spy Who Shagged Me (1999) Action|Adventure|Comedy 2683 2437 4.0 Austin Powers: The Spy Who Shagged Me (1999) Action|Adventure|Comedy 2313 2442 5.0 Elephant Man, The (1980) Drama 2683 2444 4.5 Austin Powers: The Spy Who Shagged Me (1999) Action|Adventure|Comedy 4958 2444 4.5 Behind Enemy Lines (2001) Action|Drama|War 1201 2448 5.0 Good, the Bad and the Ugly, The (Buono, il brutto, il cattivo, Il) (1966) Action|Adventure|Western 50804 2449 0.5 Hannibal Rising (2007) Drama|Horror|Thriller 57274 2449 4.5 [REC] (2007) Drama|Horror|Thriller 1892 2451 3.0 Perfect Murder, A (1998) Thriller 2463 2451 2.0 Ruthless People (1986) Comedy 2683 2451 3.0 Austin Powers: The Spy Who Shagged Me (1999) Action|Adventure|Comedy 3841 2451 1.0 Air America (1990) Action|Comedy 2683 2452 2.0 Austin Powers: The Spy Who Shagged Me (1999) Action|Adventure|Comedy 2683 2453 4.0 Austin Powers: The Spy Who Shagged Me (1999) Action|Adventure|Comedy 7325 2453 3.5 Starsky & Hutch (2004) Action|Comedy|Crime|Thriller 1441 2456 3.0 Benny & Joon (1993) Comedy|Romance 2683 2459 3.0 Austin Powers: The Spy Who Shagged Me (1999) Action|Adventure|Comedy 1441 2460 4.0 Benny & Joon (1993) Comedy|Romance 2052 2460 0.5 Hocus Pocus (1993) Children|Comedy|Fantasy|Horror 2313 2460 3.0 Elephant Man, The (1980) Drama 2683 2460 3.5 Austin Powers: The Spy Who Shagged Me (1999) Action|Adventure|Comedy 2683 2463 3.0 Austin Powers: The Spy Who Shagged Me (1999) Action|Adventure|Comedy 7325 2463 2.0 Starsky & Hutch (2004) Action|Comedy|Crime|Thriller 7460 2463 4.0 Coffee and Cigarettes (2003) Comedy|Drama 1201 2464 4.0 Good, the Bad and the Ugly, The (Buono, il brutto, il cattivo, Il) (1966) Action|Adventure|Western 1441 2464 5.0 Benny & Joon (1993) Comedy|Romance 1892 2464 4.0 Perfect Mu

In [0]:
df_rating=df_rating_per_user_movies.groupBy('userId','movieId','title','genres').max('max_rating')
display(df_rating)

userId movieId title genres max(max_rating) 18580 3175 Galaxy Quest (1999) Adventure|Comedy|Sci-Fi 3.5 18580 6620 American Splendor (2003) Comedy|Drama 3.0 18580 8638 Before Sunset (2004) Drama|Romance 3.5 18580 32460 Knockin' on Heaven's Door (1997) Action|Comedy|Crime|Drama 2.0 18580 33722 Ladies in Lavender (2004) Comedy|Drama|Romance 4.5 18580 36525 Just Like Heaven (2005) Comedy|Fantasy|Romance 3.5 18580 54190 Across the Universe (2007) Drama|Fantasy|Musical|Romance 3.0 18580 68135 17 Again (2009) Comedy|Drama 3.5 18580 160563 The Legend of Tarzan (2016) Action|Adventure 4.0 18580 166558 Underworld: Blood Wars (2016) Action|Horror 3.0 18580 175197 The Dark Tower (2017) Fantasy|Horror|Sci-Fi|Western 4.0 18583 471 Hudsucker Proxy, The (1994) Comedy 3.0 18583 1342 Candyman (1992) Horror|Thriller 2.5 18583 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 3.0 18583 3175 Galaxy Quest (1999) Adventure|Comedy|Sci-Fi 4.0 18583 6620 American Splendor (2003) Comedy|Drama 3.0 18583 8638 Before Sunset (2004) Drama|Romance 3.0 18584 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 3.5 18585 3997 Dungeons & Dragons (2000) Action|Adventure|Comedy|Fantasy 5.0 18588 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 3.0 18588 54190 Across the Universe (2007) Drama|Fantasy|Musical|Romance 4.0 18589 471 Hudsucker Proxy, The (1994) Comedy 2.0 18592 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 5.0 18592 3175 Galaxy Quest (1999) Adventure|Comedy|Sci-Fi 5.0 18597 1645 The Devil's Advocate (1997) Drama|Mystery|Thriller 4.0 18598 496 What Happened Was... (1994) Comedy|Drama|Romance|Thriller 1.0 18599 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 4.0 18599 4519 Land Before Time, The (1988) Adventure|Animation|Children|Fantasy 3.5 18602 471 Hudsucker Proxy, The (1994) Comedy 5.0 18602 1645 The Devil's Advocate (1997) Drama|Mystery|Thriller 5.0 18602 44022 Ice Age 2: The Meltdown (2006) Adventure|Animation|Children|Comedy 3.0 18602 96488 Searching for Sugar Man (2012) Documentary 5.0 18603 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 4.5 18603 1645 The Devil's Advocate (1997) Drama|Mystery|Thriller 4.5 18606 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 4.0 18606 3918 Hellbound: Hellraiser II (1988) Horror 3.0 18612 3175 Galaxy Quest (1999) Adventure|Comedy|Sci-Fi 4.0 18617 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 4.5 18618 471 Hudsucker Proxy, The (1994) Comedy 3.5 18618 1959 Out of Africa (1985) Drama|Romance 2.0 18618 7833 Shadow of the Thin Man (1941) Comedy|Crime|Mystery 4.5 18622 2142 American Tail: Fievel Goes West, An (1991) Adventure|Animation|Children|Musical|Western 4.5 18622 68135 17 Again (2009) Comedy|Drama 4.5 18625 1088 Dirty Dancing (1987) Drama|Musical|Romance 3.0 18625 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 3.0 18628 148 Awfully Big Adventure, An (1995) Drama 2.0 18628 463 Guilty as Sin (1993) Crime|Drama|Thriller 3.0 18628 471 Hudsucker Proxy, The (1994) Comedy 4.0 18628 496 What Happened Was... (1994) Comedy|Drama|Romance|Thriller 5.0 18628 1088 Dirty Dancing (1987) Drama|Musical|Romance 5.0 18628 1238 Local Hero (1983) Comedy 5.0 18628 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 4.0 18628 1645 The Devil's Advocate (1997) Drama|Mystery|Thriller 3.0 18628 1959 Out of Africa (1985) Drama|Romance 4.0 18628 2866 Buddy Holly Story, The (1978) Drama 5.0 18628 3175 Galaxy Quest (1999) Adventure|Comedy|Sci-Fi 3.0 18628 3794 Chuck & Buck (2000) Comedy|Drama 4.0 18628 6357 High Society (1956) Comedy|Musical|Romance 3.0 18628 6620 American Splendor (2003) Comedy|Drama 4.0 18628 8638 Before Sunset (2004) Drama|Romance 5.0 18628 26425 In-Laws, The (1979) Action|Comedy 4.5 18628 54190 Across the Universe (2007) Drama|Fantasy|Musical|Romance 5.0 18630 2122 Children of the Corn (1984) Horror|Thriller 0.5 18630 3175 Galaxy Quest (1999) Adventure|Comedy|Sci-Fi 2.0 18631 4519 Land Before Time, The (1988) Adventure|A

Out[70]: 4610081

In [0]:
#Let us filter out movies with less that 4 rating.
df_rating=df_rating.withColumnRenamed('max(max_rating)','max_rating_1')
df_rating=df_rating.filter(df_rating['max_rating_1']>4)
display(df_rating)

userId movieId title genres max_rating_1 18580 33722 Ladies in Lavender (2004) Comedy|Drama|Romance 4.5 18585 3997 Dungeons & Dragons (2000) Action|Adventure|Comedy|Fantasy 5.0 18592 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 5.0 18592 3175 Galaxy Quest (1999) Adventure|Comedy|Sci-Fi 5.0 18602 471 Hudsucker Proxy, The (1994) Comedy 5.0 18602 1645 The Devil's Advocate (1997) Drama|Mystery|Thriller 5.0 18602 96488 Searching for Sugar Man (2012) Documentary 5.0 18603 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 4.5 18603 1645 The Devil's Advocate (1997) Drama|Mystery|Thriller 4.5 18617 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 4.5 18618 7833 Shadow of the Thin Man (1941) Comedy|Crime|Mystery 4.5 18622 2142 American Tail: Fievel Goes West, An (1991) Adventure|Animation|Children|Musical|Western 4.5 18622 68135 17 Again (2009) Comedy|Drama 4.5 18628 496 What Happened Was... (1994) Comedy|Drama|Romance|Thriller 5.0 18628 1088 Dirty Dancing (1987) Drama|Musical|Romance 5.0 18628 1238 Local Hero (1983) Comedy 5.0 18628 2866 Buddy Holly Story, The (1978) Drama 5.0 18628 8638 Before Sunset (2004) Drama|Romance 5.0 18628 26425 In-Laws, The (1979) Action|Comedy 4.5 18628 54190 Across the Universe (2007) Drama|Fantasy|Musical|Romance 5.0 18633 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 5.0 18639 3175 Galaxy Quest (1999) Adventure|Comedy|Sci-Fi 5.0 18641 2366 King Kong (1933) Action|Adventure|Fantasy|Horror 4.5 18642 3175 Galaxy Quest (1999) Adventure|Comedy|Sci-Fi 4.5 18643 44022 Ice Age 2: The Meltdown (2006) Adventure|Animation|Children|Comedy 5.0 18645 2142 American Tail: Fievel Goes West, An (1991) Adventure|Animation|Children|Musical|Western 4.5 18645 3175 Galaxy Quest (1999) Adventure|Comedy|Sci-Fi 5.0 18645 4519 Land Before Time, The (1988) Adventure|Animation|Children|Fantasy 5.0 18645 54190 Across the Universe (2007) Drama|Fantasy|Musical|Romance 4.5 18650 1959 Out of Africa (1985) Drama|Romance 4.5 18651 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 5.0 18663 1238 Local Hero (1983) Comedy 5.0 18677 471 Hudsucker Proxy, The (1994) Comedy 5.0 18685 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 5.0 18686 2366 King Kong (1933) Action|Adventure|Fantasy|Horror 5.0 18689 26425 In-Laws, The (1979) Action|Comedy 5.0 18702 471 Hudsucker Proxy, The (1994) Comedy 4.5 18705 54190 Across the Universe (2007) Drama|Fantasy|Musical|Romance 4.5 18718 8638 Before Sunset (2004) Drama|Romance 5.0 18722 1645 The Devil's Advocate (1997) Drama|Mystery|Thriller 5.0 18740 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 4.5 18747 1959 Out of Africa (1985) Drama|Romance 5.0 18752 1645 The Devil's Advocate (1997) Drama|Mystery|Thriller 4.5 18768 8638 Before Sunset (2004) Drama|Romance 4.5 18779 44022 Ice Age 2: The Meltdown (2006) Adventure|Animation|Children|Comedy 5.0 18782 3175 Galaxy Quest (1999) Adventure|Comedy|Sci-Fi 4.5 18796 8638 Before Sunset (2004) Drama|Romance 5.0 18798 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 4.5 18806 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 4.5 18806 44022 Ice Age 2: The Meltdown (2006) Adventure|Animation|Children|Comedy 5.0 18808 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 5.0 18822 3175 Galaxy Quest (1999) Adventure|Comedy|Sci-Fi 5.0 18828 1088 Dirty Dancing (1987) Drama|Musical|Romance 5.0 18828 3175 Galaxy Quest (1999) Adventure|Comedy|Sci-Fi 4.5 18836 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 5.0 18850 471 Hudsucker Proxy, The (1994) Comedy 5.0 18857 1645 The Devil's Advocate (1997) Drama|Mystery|Thriller 4.5 18867 1088 Dirty Dancing (1987) Drama|Musical|Romance 4.5 18868 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 5.0 18869 1580 Men in Black (a.k.a. MIB) (1997) Action|Comedy|Sci-Fi 5.0 18869 1645 The Devil's Advocate (1997) Drama|Mystery|Thriller 5.0 18869 3175 Galaxy Quest (1999) Adventure|Comedy|Sci-Fi 5.0 18877 1088 Dirty Dancing (1987) 

In [0]:
#Identifying the best movies, classifies in genres
df_movies_per_genre=df_rating.groupBy('genres','title').count()
df_movies_per_genre.dropDuplicates()
display(df_movies_per_genre)

genres title count Comedy|Drama American Splendor (2003) 173 Drama|Romance Reader, The (2008) 123 Drama|Mystery|Thriller Insomnia (1997) 48 Drama Margot at the Wedding (2007) 2 Adventure|Comedy|Crime Miss Congeniality 2: Armed and Fabulous (2005) 18 Action|Crime|Thriller Safe (2012) 15 Drama Regarding Henry (1991) 15 Comedy|Horror|Thriller Mute Witness (1994) 14 Drama Bright Lights, Big City (1988) 4 Drama Brokedown Palace (1999) 13 Action|Adventure|Drama Sanjuro (Tsubaki Sanjûrô) (1962) 127 Crime|Thriller Heaven's Prisoners (1996) 9 Comedy|Drama Wish I Was Here (2014) 4 Comedy|Horror Creep 2 (2017) 4 Action|Romance Once Upon a Time in China II (Wong Fei-hung Ji Yi: Naam yi dong ji keung) (1992) 12 Drama Cool Hand Luke (1967) 893 Comedy|Drama|Romance Waitress (2007) 45 Comedy|Crime Very Bad Things (1998) 27 Action|Drama|Horror Dawn of the Dead (1978) 231 Comedy|Drama|Romance Love & Sex (2000) 8 Children|Comedy|Romance Princess Diaries, The (2001) 132 Drama Personal Velocity (2002) 10 Action Red Scorpion (1989) 1 Adventure|Animation|Children|Comedy|Sci-Fi Grand Day Out with Wallace and Gromit, A (1989) 597 Drama Strawberry and Chocolate (Fresa y chocolate) (1993) 36 Horror Martyrs (2008) 31 Drama Elephant Man, The (1980) 445 Drama|Romance Sweet November (2001) 39 Drama|Romance Brokeback Mountain (2005) 410 Drama Whiplash (2014) 1065 Adventure|Animation|Children|Musical|Western American Tail: Fievel Goes West, An (1991) 31 Comedy|Drama|Romance Julie & Julia (2009) 90 Children|Comedy D3: The Mighty Ducks (1996) 18 Comedy|Musical Sarah Silverman: Jesus Is Magic (2005) 10 Horror|Mystery|Thriller Saw VII 3D - The Final Chapter (2010) 20 Comedy|Romance Blame It on Rio (1984) 12 Drama|Thriller|War Valkyrie (2008) 57 Comedy Bridesmaids (2011) 167 Drama My Bodyguard (1980) 40 Drama|Romance Black Orpheus (Orfeu Negro) (1959) 26 Comedy|Crime Scotland, Pa. (2001) 6 Action|Adventure|Drama|War Big Red One, The (1980) 20 Comedy|Romance Boys and Girls (2000) 9 Mystery|Thriller Shattered (1991) 4 Action|Comedy In-Laws, The (1979) 25 Comedy|Romance The Big Sick (2017) 81 Comedy|Drama|Romance Prizzi's Honor (1985) 63 Action|Adventure The Legend of Tarzan (2016) 16 Comedy|Romance 10 Things I Hate About You (1999) 517 Drama|Thriller|War Eye in the Sky (2016) 24 Action|Adventure|Fantasy Warcraft (2016) 43 Comedy|Drama Storytelling (2001) 30 Comedy|Romance Sidewalks of New York (2001) 4 Action|Comedy MacGruber (2010) 7 Drama Affliction (1997) 53 Comedy|Mystery Who's Harry Crumb? (1989) 10 Documentary Hearts of Darkness: A Filmmakers Apocalypse (1991) 74 Drama Ratcatcher (1999) 11 Romance Before We Go (2014) 10 Drama|Horror|Mystery|Thriller Tale of Two Sisters, A (Janghwa, Hongryeon) (2003) 33 Action Red Heat (1988) 11 Mystery|Thriller Eyes of Laura Mars (1978) 8 Comedy|Drama Butcher Boy, The (1997) 44 Action|Crime|Drama|Thriller Unleashed (Danny the Dog) (2005) 44 Drama|Mystery|Thriller Number 23, The (2007) 56 Action|Drama|Horror|IMAX World War Z (2013) 175 Crime|Drama|Mystery|Romance|Thriller Secret in Their Eyes, The (El secreto de sus ojos) (2009) 160 Horror|Thriller Wolfman, The (2010) 5 Crime|Drama Godfather, The (1972) 6033 Comedy|Drama Tin Men (1987) 49 Drama|Thriller Straw Dogs (1971) 60 Crime|Drama|Horror|Thriller Exorcism of Emily Rose, The (2005) 25 Drama|Sci-Fi|Thriller Gattaca (1997) 1185 Action|Comedy Air America (1990) 10 Drama|Romance Walk to Remember, A (2002) 117 Drama|Mystery Awakenings (1990) 330 Comedy Spy Hard (1996) 66 Action|Adventure|Comedy|Fantasy|Sci-Fi Ant-Man and the Wasp (2018) 63 Comedy|Drama|Fantasy|Mystery Bothersome Man, The (Brysomme mannen, Den) (2006) 20 Comedy|Drama|Romance Living Out Loud (1998) 21 Horror Dracula (1931) 93 Crime|Drama|Romance Thieves (Voleurs, Les) (1996) 7 Comedy|Documentary It Came from Hollywood (1982) 4 Drama|Romance Angels and Insects (1995) 72 Action|Drama Death Wish 2 (1982) 8 Children Zeus and Roxanne (1997) 4 Horror|Thriller The Boy (2016) 7 Comedy|Drama Breaking Away (1979) 214 Action

In [0]:
#Identifying Genre for specific users
df_rating_genre=df_rating.select('userId','title','genres').groupBy('userId','genres').count()

In [0]:
display(df_rating_genre)

userId genres count 18622 Comedy|Drama 1 18677 Comedy 4 19042 Action|Comedy 1 19536 Comedy|Fantasy|Romance 2 20470 Adventure|Comedy|Sci-Fi 1 21365 Drama|Romance 35 21800 Drama|Fantasy|Musical|Romance 1 21982 Action|Comedy|Sci-Fi 1 22051 Adventure|Animation|Children|Comedy 2 22392 Action|Comedy|Sci-Fi 2 23529 Drama|Musical|Romance 1 19472 Drama|Mystery|Sci-Fi|Thriller 1 19775 Action|Adventure|Sci-Fi|Thriller 4 20834 Action|Drama|Thriller|War 1 21882 Drama|Romance 7 22522 Crime|Drama 4 22916 Drama|Mystery|Sci-Fi|Thriller 1 23827 Thriller 1 23865 Action|Adventure|Sci-Fi|Thriller 1 17384 Adventure|Comedy|Sci-Fi 3 21826 Action|Drama|Romance|Sci-Fi 1 22511 Documentary 1 23342 Adventure|Comedy|Sci-Fi 2 23724 Adventure|Drama 1 23931 Comedy|Romance 5 16858 Comedy|Fantasy|Romance 1 17720 Adventure|Comedy|Drama 1 18412 Adventure|Comedy|Drama 2 20475 Adventure|Comedy|Drama 1 22496 Adventure|Comedy|Drama 1 23319 Adventure|Comedy|Drama 1 23502 Comedy|Fantasy|Romance 1 16726 Action|Adventure|Sci-Fi|Thriller|IMAX 2 18550 Drama 5 19042 Adventure|Animation|Children|Comedy|Sci-Fi 1 19657 Comedy|Fantasy 1 20933 Action|Crime|Thriller 2 23838 Adventure|Animation|Children|Comedy|Sci-Fi 1 20392 Drama|War 5 20958 Drama|War 7 21041 Adventure|Animation|Children|Comedy|Musical 2 21064 Adventure|Animation|Children|Comedy|Musical 1 21616 Adventure|Animation|Children|Comedy|Musical 1 22253 Adventure|Comedy|Crime|Drama|Romance 1 24085 Crime|Drama|Thriller 1 24099 Drama|War 3 17418 Comedy|Crime|Drama|Thriller 1 17648 Comedy|Crime|Drama|Thriller 1 17712 Action|Adventure|Comedy|Crime 1 17795 Comedy|Crime|Drama|Thriller 1 18318 Comedy|Crime|Drama|Thriller 1 18727 Comedy|Crime|Drama|Thriller 1 19162 Comedy|Crime|Drama|Thriller 1 20331 Comedy|Crime|Drama|Thriller 1 20338 Comedy|Crime|Thriller 2 20780 Comedy|Crime|Drama|Thriller 1 22353 Comedy|Crime|Drama|Thriller 1 23551 Comedy|Crime|Drama|Thriller 1 23797 Drama 2 16658 Action|Thriller 2 17213 Adventure|Animation|Children|Drama 2 17812 Comedy|Drama|Romance 1 19318 Action|Adventure|Sci-Fi|Thriller 2 22284 Action|Adventure|Sci-Fi|Thriller 2 23658 Animation|Comedy|Musical 2 23882 Adventure|Animation|Children|Drama 1 17472 Action|Crime|Drama|IMAX 1 18484 Comedy|Romance 17 18563 Horror|Thriller 1 18751 Action|Crime|Drama|IMAX 1 18896 Action|Crime|Drama|IMAX 1 19043 Action|Crime|Drama|IMAX 1 22366 Action|Crime|Drama|IMAX 1 22776 Action|Crime|Drama|IMAX 1 22970 Adventure|Children|Romance 1 17042 Crime|Horror|Thriller 1 16655 Crime|Horror|Thriller 1 17262 Crime|Horror|Thriller 1 18001 Crime|Horror|Thriller 1 19156 Fantasy|Sci-Fi 1 19242 Film-Noir|Mystery|Thriller 1 19455 Crime|Horror|Thriller 1 19861 Crime|Horror|Thriller 1 20316 Crime|Horror|Thriller 1 20690 Drama|Sci-Fi|Thriller 1 20868 Crime|Horror|Thriller 1 20871 Crime|Horror|Thriller 1 21648 Crime|Horror|Thriller 1 21912 Drama|Sci-Fi|Thriller 3 23423 Comedy|Drama|Fantasy|Romance 1 24271 Drama 1 17474 Comedy|Horror 16 21349 Adventure|Animation|Children|Comedy|Fantasy 2 22731 Adventure|Drama|War 1 23089 Action|Fantasy|Horror 1 17565 Action|Adventure 2 17716 Children|Drama 2 18338 Action|Adventure|Animation|Children|Comedy 1 18584 Action|Adventure 2 18776 Action|Adventure 1 18827 Action|Adventure 2 19639 Drama 3 20913 Action|Adventure 2 23002 Action|Adventure|Animation|Children|Comedy 1 23521 Action|Adventure 3 23913 Action|Adventure 1 24415 Action|Adventure 1 16886 Action|Comedy|Western 1 16638 Adventure|Children|Fantasy 2 19049 Documentary 1 19389 Adventure|Drama 1 23336 Adventure|Drama 1 23763 Crime|Drama|Mystery|Romance|Thriller 1 19073 Action|Adventure|Comedy 1 19744 Comedy|Documentary 1 22630 Action|Adventure|Comedy 2 23123 Action|Adventure|Western 1 20582 Drama|Fantasy|Romance 1 21321 Drama|Fantasy|Romance 7 21468 Drama|Romance|Sci-Fi 2 23951 Documentary 2 16804 Drama 12 17681 Action|Adventure|Sci-Fi 11 16746 Action|Comedy|Horror 1 18837 Comedy|Drama|Fantasy|Romance|Thriller 1 19010 Action|Comedy|Horror 1 19462 Comedy|Romance 6 21393 Action|Adventure|Sci-Fi 1 18

In [0]:
df_recent_movies=df_ratings.groupBy('userId','movieId').agg(f.max(df_ratings['rating_date']))

In [0]:
display(df_recent_movies)

userId movieId max(rating_date) 3 5004 null 3 6754 null 3 35836 null 3 87232 null 4 3624 null 4 122882 null 5 1246 null 6 2028 null 8 1777 1998-07-21 11 48043 null 12 778 null 12 1951 null 12 27815 2006-10-31 12 40278 null 12 42018 null 13 2716 null 13 5903 null 15 2387 null 18 95 null 18 1721 null 18 4963 2005-05-13 19 26417 null 19 81018 2015-06-19 21 68237 null 22 329 null 23 514 1999-08-20 23 2289 1999-08-20 23 2707 null 31 349 null 31 4085 2009-03-22 32 454 null 34 1207 2011-07-04 35 160980 null 38 4306 null 38 26776 null 39 3608 null 41 1429 null 46 2268 null 46 3135 null 46 4710 2009-10-23 58 72378 2012-09-16 63 4447 null 67 2193 null 72 1250 null 72 2762 null 72 3760 null 72 4130 2001-12-29 75 2469 2018-04-20 80 260 null 80 3247 null 80 3598 2001-11-22 80 4266 null 81 2539 null 82 527 null 82 3000 2015-01-18 82 6537 null 82 68442 null 84 27788 null 91 106916 null 92 2353 null 93 7380 2017-02-03 96 96821 null 108 58559 2018-05-17 109 163645 null 117 54259 null 123 2502 null 125 2478 null 132 5334 null 139 1729 null 139 2571 2003-06-29 139 6365 null 142 1464 null 142 7438 null 145 2720 null 147 1127 null 147 1449 1999-03-01 150 30749 null 155 3481 null 155 5618 null 155 5679 null 155 5956 null 159 4054 null 159 4979 null 160 45722 null 164 5620 null 166 1721 null 171 3088 null 171 3795 null 175 1079 null 175 3554 null 175 4220 null 181 2699 null 181 157361 null 184 4246 null 186 648 null 187 61348 2010-01-24 204 68073 null 216 353 null 217 6333 null 222 40815 null 224 4226 null 225 59256 2010-10-01 227 88672 2011-08-15 228 2232 2011-03-10 234 107141 null 235 171763 null 240 3024 null 242 3105 2006-01-10 243 6482 null 243 100302 null 243 102033 null 260 355 2012-06-16 260 912 2012-12-16 261 1573 2001-01-05 267 30803 null 270 2770 null 272 3247 null 280 2239 null 281 913 null 284 2788 2015-01-18 284 4878 null 284 51540 null 287 1907 null 290 1968 null 290 4246 null 296 647 null 296 33679 null 296 48780 null 302 48780 null 302 88140 null 307 3526 null 313 3033 null 313 4022 null 313 5449 null 313 7255 null 316 1381 null 318 2819 null 321 3704 null 321 128360 null 322 3101 null 329 160 1996-04-25 332 3948 2003-04-12 342 318 null 357 380 2013-08-05 357 1721 null 357 52604 null 357 91630 null 357 179275 null 360 1210 1997-04-07 368 1089 2014-10-15 368 2501 2014-06-15 368 56174 null 375 44191 null 378 32587 null 379 1616 null 382 78469 2015-12-22 386 4344 2004-11-25 391 1198 null 395 2671 null 395 3072 2011-03-10 397 72998 null 402 8666 null 402 91535 null 403 179221 2018-12-20 409 8665 2005-09-27 421 1288 null 421 2003 1998-10-21 424 5218 null 426 2248 null 426 3505 null 426 4027 null 426 46972 null 426 68791 null 426 164179 null 427 47 null 431 1210 null 431 2401 null 438 595 null 439 65261 null 440 1732 null 440 3255 null 441 3186 null 443 2361 null 443 3396 null 445 76093 2016-10-07 449 90647 2017-01-10 450 718 null 450 1682 null 450 43801 null 450 77866 null 450 104414 null 460 64614 null 460 152081 2016-01-26 462 7263 null 462 34048 2006-12-30 465 3052 2005-09-21 472 1895 null 472 2012 2001-01-21 472 2395 null 476 2716 2007-05-05 477 376 null 477 6377 null 478 68954 null 489 5445 null 489 70286 null 489 73017 null 494 1917 null 494 159858 null 500 5791 2006-09-01 502 597 1996-01-22 504 1918 null 512 2805 null 512 3988 null 514 377 null 521 5782 null 523 1889 null 526 1092 null 538 8970 null 538 93326 null 541 1527 2018-07-21 541 8907 2018-07-21 541 26587 2018-07-21 541 30749 2018-07-21 541 89759 2018-07-21 541 141818 2018-07-21 541 180031 2018-07-21 541 188327 2018-07-21 544 70599 2016-07-28 548 3453 2015-09-14 548 6534 2015-10-14 548 8908 2015-10-14 548 31410 2015-09-14 548 48161 2015-10-14 548 55908 2015-10-14 548 60046 2015-09-14 548 61248 2015-10-14 548 132979 2015-08-14 550 6287 2018-04-09 551 318 null 560 2012 null 561 70 2000-11-20 561 788 null 563 2717 null 566 1573 null 566 6947 null 567 6063 null 571 64957 null 575 68135 null 576 849 null 583 7254 null 592 2504 null 598 77561 null 600 253 null 605 594 null 606 8

In [0]:
#Join above 2 datasets
df_recent_movies_1=df_rating_genre.join(df_recent_movies,['userId'],'left')
display(df_recent_movies_1)

userId genres count movieId max(rating_date) 26 Mystery|Sci-Fi|Thriller 1 2382 null 26 Mystery|Sci-Fi|Thriller 1 296 null 26 Mystery|Sci-Fi|Thriller 1 1270 null 26 Mystery|Sci-Fi|Thriller 1 54503 null 26 Mystery|Sci-Fi|Thriller 1 47 null 26 Mystery|Sci-Fi|Thriller 1 52604 null 26 Mystery|Sci-Fi|Thriller 1 3173 null 26 Mystery|Sci-Fi|Thriller 1 1991 null 26 Mystery|Sci-Fi|Thriller 1 2858 null 26 Mystery|Sci-Fi|Thriller 1 4023 null 26 Mystery|Sci-Fi|Thriller 1 780 null 26 Mystery|Sci-Fi|Thriller 1 4951 null 26 Mystery|Sci-Fi|Thriller 1 260 null 26 Mystery|Sci-Fi|Thriller 1 1210 null 26 Mystery|Sci-Fi|Thriller 1 1 null 26 Mystery|Sci-Fi|Thriller 1 2764 null 26 Mystery|Sci-Fi|Thriller 1 110 null 26 Mystery|Sci-Fi|Thriller 1 72249 null 26 Mystery|Sci-Fi|Thriller 1 1198 null 26 Mystery|Sci-Fi|Thriller 1 2571 null 26 Mystery|Sci-Fi|Thriller 1 590 null 26 Mystery|Sci-Fi|Thriller 1 356 null 26 Mystery|Sci-Fi|Thriller 1 480 null 26 Mystery|Sci-Fi|Thriller 1 2161 null 26 Mystery|Sci-Fi|Thriller 1 593 null 26 Mystery|Sci-Fi|Thriller 1 54286 null 26 Mystery|Sci-Fi|Thriller 1 455 null 26 Mystery|Sci-Fi|Thriller 1 648 null 26 Mystery|Sci-Fi|Thriller 1 318 null 26 Mystery|Sci-Fi|Thriller 1 1037 null 26 Mystery|Sci-Fi|Thriller 1 1969 null 26 Mystery|Sci-Fi|Thriller 1 79132 null 26 Mystery|Sci-Fi|Thriller 1 50 null 26 Mystery|Sci-Fi|Thriller 1 589 null 26 Mystery|Sci-Fi|Thriller 1 53322 null 26 Mystery|Sci-Fi|Thriller 1 32 null 26 Mystery|Sci-Fi|Thriller 1 377 null 26 Mystery|Sci-Fi|Thriller 1 1586 null 26 Mystery|Sci-Fi|Thriller 1 344 null 26 Crime|Drama|Mystery|Thriller 1 2382 null 26 Crime|Drama|Mystery|Thriller 1 296 null 26 Crime|Drama|Mystery|Thriller 1 1270 null 26 Crime|Drama|Mystery|Thriller 1 54503 null 26 Crime|Drama|Mystery|Thriller 1 47 null 26 Crime|Drama|Mystery|Thriller 1 52604 null 26 Crime|Drama|Mystery|Thriller 1 3173 null 26 Crime|Drama|Mystery|Thriller 1 1991 null 26 Crime|Drama|Mystery|Thriller 1 2858 null 26 Crime|Drama|Mystery|Thriller 1 4023 null 26 Crime|Drama|Mystery|Thriller 1 780 null 26 Crime|Drama|Mystery|Thriller 1 4951 null 26 Crime|Drama|Mystery|Thriller 1 260 null 26 Crime|Drama|Mystery|Thriller 1 1210 null 26 Crime|Drama|Mystery|Thriller 1 1 null 26 Crime|Drama|Mystery|Thriller 1 2764 null 26 Crime|Drama|Mystery|Thriller 1 110 null 26 Crime|Drama|Mystery|Thriller 1 72249 null 26 Crime|Drama|Mystery|Thriller 1 1198 null 26 Crime|Drama|Mystery|Thriller 1 2571 null 26 Crime|Drama|Mystery|Thriller 1 590 null 26 Crime|Drama|Mystery|Thriller 1 356 null 26 Crime|Drama|Mystery|Thriller 1 480 null 26 Crime|Drama|Mystery|Thriller 1 2161 null 26 Crime|Drama|Mystery|Thriller 1 593 null 26 Crime|Drama|Mystery|Thriller 1 54286 null 26 Crime|Drama|Mystery|Thriller 1 455 null 26 Crime|Drama|Mystery|Thriller 1 648 null 26 Crime|Drama|Mystery|Thriller 1 318 null 26 Crime|Drama|Mystery|Thriller 1 1037 null 26 Crime|Drama|Mystery|Thriller 1 1969 null 26 Crime|Drama|Mystery|Thriller 1 79132 null 26 Crime|Drama|Mystery|Thriller 1 50 null 26 Crime|Drama|Mystery|Thriller 1 589 null 26 Crime|Drama|Mystery|Thriller 1 53322 null 26 Crime|Drama|Mystery|Thriller 1 32 null 26 Crime|Drama|Mystery|Thriller 1 377 null 26 Crime|Drama|Mystery|Thriller 1 1586 null 26 Crime|Drama|Mystery|Thriller 1 344 null 26 Mystery|Thriller 1 2382 null 26 Mystery|Thriller 1 296 null 26 Mystery|Thriller 1 1270 null 26 Mystery|Thriller 1 54503 null 26 Mystery|Thriller 1 47 null 26 Mystery|Thriller 1 52604 null 26 Mystery|Thriller 1 3173 null 26 Mystery|Thriller 1 1991 null 26 Mystery|Thriller 1 2858 null 26 Mystery|Thriller 1 4023 null 26 Mystery|Thriller 1 780 null 26 Mystery|Thriller 1 4951 null 26 Mystery|Thriller 1 260 null 26 Mystery|Thriller 1 1210 null 26 Mystery|Thriller 1 1 null 26 Mystery|Thriller 1 2764 null 26 Mystery|Thriller 1 110 null 26 Mystery|Thriller 1 72249 null 26 Mystery|Thriller 1 1198 null 26 Mystery|Thriller 1 2571 null 26 Mystery|Thriller 1 590 null 26 Mystery|Thriller 1 356 null 26 Mystery|Thriller 1 480 null 26 Mystery|Thriller 1 216